In [2]:
import math
import random
import numpy as np
import torch
import torch.nn as nn
import torch.optim as optim
import torch.nn.functional as F
import torch.distributions
from collections import namedtuple
from itertools import count

device = "cuda"

batchsize = 512
nsamples = 8
npoints = 5
emsize = 512


class Graph_Transformer(nn.Module):
    def __init__(self, emsize = 64, nhead = 8, nhid = 1024, nlayers = 4, ndecoderlayers = 0, dropout = 0):
        super().__init__()
        self.emsize = emsize
        from torch.nn import TransformerEncoder, TransformerEncoderLayer, TransformerDecoder, TransformerDecoderLayer
        encoder_layers = TransformerEncoderLayer(emsize, nhead, nhid, dropout = dropout)
        decoder_layers = TransformerDecoderLayer(emsize, nhead, nhid, dropout = dropout)
        self.transformer_encoder = TransformerEncoder(encoder_layers, nlayers)
        self.transformer_decoder = TransformerDecoder(decoder_layers, ndecoderlayers)
        self.encoder = nn.Linear(2, emsize)
        self.outputattention_query = nn.Linear(emsize, emsize, bias = False)
        self.outputattention_key = nn.Linear(emsize, emsize, bias = False)
        self.start_token = nn.Parameter(torch.randn([emsize], device = device))
        
        self.lineartest0 = nn.Linear(2, emsize)
        self.lineartest1 = nn.Linear(2, emsize)
        self.lineartest2 = nn.Linear(2, emsize)
        self.lineartest3 = nn.Linear(2 * emsize, emsize)
    
    def generate_subsequent_mask(self, sz):
        mask = torch.tril(torch.ones([sz, sz], dtype = torch.bool, device = device), diagonal = 0) #first index < second index for True. True means target (first index) does not get any value from the source (second index)
    
    def encode(self, src): #src must be [batchsize * nsamples, npoints, 2]
        src = self.encoder(src).transpose(0, 1)
        output = self.transformer_encoder(src)
        return output #[npoints, batchsize * nsamples, emsize]
    
    def test_encode(self, src): #src must be [batchsize * nsamples, npoints = 5, 2]
        point_1 = self.lineartest1(src[:, 3, :] - 0.5) #want mean 0!!!!
        point_2 = self.lineartest1(src[:, 4, :] - 0.5)
        remaining = self.lineartest0(src[:, :3, :]) #[batchsize * nsamples, 3, emsize]
        point_1_message = self.lineartest1(src[:, 3, :] - 0.5).squeeze(1)
        point_2_message = self.lineartest2(src[:, 4, :] - 0.5).squeeze(1)
        point_1 = F.relu(torch.cat([point_1, point_2_message], dim = 1))
        point_2 = F.relu(torch.cat([point_2, point_1_message], dim = 1))
        point_1 = self.lineartest3(point_1)
        point_2 = self.lineartest3(point_2)
        src = torch.cat([torch.zeros_like(remaining.transpose(0, 1)), point_1.unsqueeze(0), point_2.unsqueeze(0)])
        return src #[npoints = 5, batchsize * nsamples, emsize]
    
    def decode_next(self, memory, tgt, route_mask): #route mask is [batchsize * nsamples, npoints], both memory and tgt must have batchsize and nsamples in same dimension (the 1th one)
        npoints = memory.size(0)
        batchsize = tgt.size(1)
        """if I really wanted this to be efficient I'd only recompute the decoder for the last tgt, and just remebering what the others looked like from before (won't change due to mask)"""
        """have the option to freeze the autograd on all but the last part of tgt, although at the moment this is a very natural way to say: initial choices matter more"""
        tgt_mask = self.generate_subsequent_mask(tgt.size(0))
        output = self.transformer_decoder(tgt, memory, tgt_mask) #[tgt, batchsize * nsamples, emsize]
        output_query = self.outputattention_query(memory).transpose(0, 1) #[batchsize * nsamples, npoints, emsize]
        output_key = self.outputattention_key(output[-1]) #[batchsize * nsamples, emsize]
        output_attention = torch.matmul(output_query * self.emsize ** -0.5, output_key.unsqueeze(-1)).squeeze(-1) #[batchsize * nsamples, npoints], technically don't need to scale attention as we divide by variance next anyway
        output_attention_tanh = output_attention.tanh() #[batchsize * nsamples, npoints]
        
        #we clone the route_mask incase we want to backprop using it (else it was modified by inplace opporations)
        output_attention = output_attention.masked_fill(route_mask.clone(), float('-inf')) #[batchsize * nsamples, npoints]
        output_attention_tanh = output_attention_tanh.masked_fill(route_mask.clone(), float('-inf')) #[batchsize * nsamples, npoints]
        
        return output_attention_tanh, output_attention #[batchsize * nsamples, npoints]
    
    def calculate_logprob(self, memory, routes): #memory is [npoints, batchsize * nsamples, emsize], routes is [batchsize * nsamples, npoints - 3], rather than backproping the entire loop, this saves vram (and computation)
        npoints = memory.size(0)
        ninternalpoints = routes.size(1)
        bigbatchsize = memory.size(1)
        memory_ = memory.gather(0, routes.transpose(0, 1).unsqueeze(2).expand(-1, -1, self.emsize)) #[npoints - 3, batchsize * nsamples, emsize] reorder memory into order of routes
        tgt = torch.cat([self.start_token.unsqueeze(0).unsqueeze(1).expand(1, bigbatchsize, -1), memory_[:-1]]) #[npoints - 3, batchsize * nroutes, emsize], want to go from memory to tgt
        tgt_mask = self.generate_subsequent_mask(ninternalpoints)
        output = self.transformer_decoder(tgt, memory, tgt_mask) #[npoints - 3, batchsize * nsamples, emsize]
        """want probability of going from key to query, but first need to normalise (softmax with mask)"""
        output_query = self.outputattention_query(memory_).transpose(0, 1) #[batchsize * nsamples, npoints - 3, emsize]
        output_key = self.outputattention_key(output).transpose(0, 1) #[batchsize * nsamples, npoints - 3, emsize]
        attention_mask = torch.full([ninternalpoints, ninternalpoints], True, device = device).triu(1) #[npoints - 3, npoints - 3], True for i < j
        output_attention = torch.matmul(output_query * self.emsize ** -0.5, output_key.transpose(-1, -2))
        """quick fix to stop divergence"""
        output_attention_tanh = output_attention.tanh()
        
        output_attention_tanh = output_attention_tanh.masked_fill(attention_mask, float('-inf'))
        output_attention_tanh = output_attention_tanh - output_attention_tanh.logsumexp(-2, keepdim = True) #[batchsize * nsamples, npoints - 3, npoints - 3]
        
        output_attention = output_attention.masked_fill(attention_mask, float('-inf'))
        output_attention = output_attention - output_attention.logsumexp(-2, keepdim = True) #[batchsize * nsamples, npoints - 3, npoints - 3]
        
        """infact I'm almost tempted to not mask choosing a previous point, so it's forced to learn it and somehow incorporate it into its computation, but without much impact on reinforcing good examples"""
        logprob_tanh = output_attention_tanh.diagonal(dim1 = -1, dim2 = -2).sum(-1) #[batchsize * nsamples]
        logprob = output_attention.diagonal(dim1 = -1, dim2 = -2).sum(-1) #[batchsize * nsamples]
        return logprob_tanh, logprob #[batchsize * nsamples]

NN = Graph_Transformer().to(device)
optimizer = optim.Adam(NN.parameters())


class environment():
    def reset(self, npoints, batchsize, nsamples):
        if npoints <= 3:
            print("Error: not enough points for valid problem instance")
            return
        self.batchsize = batchsize * nsamples #so that I don't have to rewrite all this code, we store these two dimensions together
        self.nsamples = nsamples
        self.npoints = npoints
        self.points = torch.rand([batchsize, npoints - 3, 2], device = device).unsqueeze(1).expand(-1, nsamples, -1, -1).reshape(self.batchsize, npoints - 3, 2)
        self.corner_points = torch.tensor([[0, 0], [2, 0], [0, 2]], dtype = torch.float, device = device)
        self.points = torch.cat([self.corner_points.unsqueeze(0).expand(self.batchsize, -1, -1), self.points], dim = -2) #[batchsize * nsamples, npoints, 2]
        self.points_mask = torch.cat([torch.ones([self.batchsize, 3], dtype = torch.bool, device = device), torch.zeros([self.batchsize, npoints - 3], dtype = torch.bool, device = device)], dim = 1)
        self.points_sequence = torch.empty([self.batchsize, 0], dtype = torch.long, device = device)
        
        """use a trick, for the purpose of an 'external' triangle that is always left untouched, which means we don't have to deal with boundary edges as being different. external triangle is [0, 1, 2] traversed clockwise..."""
        self.partial_delaunay_triangles = torch.tensor([[0, 2, 1], [0, 1, 2]], dtype = torch.int64, device = device).unsqueeze(0).expand(self.batchsize, -1, -1).contiguous() #[batchsize, ntriangles, 3] contains index of points, always anticlockwise
        self.partial_delaunay_edges = torch.tensor([5, 4, 3, 2, 1, 0], dtype = torch.int64, device = device).unsqueeze(0).expand(self.batchsize, -1).contiguous() #[batchsize, ntriangles * 3] contains location of corresponding edge (edges go in order 01, 12, 20). Edges will always flip since triangles are stored anticlockwise.
        
        self.ntriangles = 2 #can store as scalar, since will always be the same
        self.cost = torch.zeros([self.batchsize], device = device)
        
        self.logprob = torch.zeros([self.batchsize], device = device, requires_grad = True)
    
    def update(self, point_index): #point_index is [batchsize]
        if point_index.size(0) != self.batchsize:
            print("Error: point_index.size() doesn't match expected size, should be [batchsize]")
            return
        if self.points_mask.gather(1, point_index.unsqueeze(1)).sum():
            print("Error: some points already added")
            return
        triangles_coordinates = self.points.gather(1, self.partial_delaunay_triangles.view(self.batchsize, self.ntriangles * 3).unsqueeze(2).expand(-1, -1, 2)).view(self.batchsize, self.ntriangles, 3, 2) #[batchsize, ntriangles, 3, 2]
        newpoint = self.points.gather(1, point_index.unsqueeze(1).unsqueeze(2).expand(self.batchsize, 1, 2)).squeeze(1) #[batchsize, 2]
        
        incircle_matrix = torch.cat([triangles_coordinates, newpoint.unsqueeze(1).unsqueeze(2).expand(-1, self.ntriangles, 1, -1)], dim = -2) #[batchsize, ntriangles, 4, 2]
        incircle_matrix = torch.cat([incircle_matrix, (incircle_matrix * incircle_matrix).sum(-1, keepdim = True), torch.ones([self.batchsize, self.ntriangles, 4, 1], device = device)], dim = -1) #[batchsize, ntriangles, 4, 4]
        incircle_test = incircle_matrix.det() > 0 #[batchsize, ntriangles], is True if inside incircle
        removed_edge_mask = incircle_test.unsqueeze(2).expand(-1, -1, 3).reshape(-1) #[batchsize * ntriangles * 3]
        
        edges = (self.partial_delaunay_edges + self.ntriangles * 3 * torch.arange(self.batchsize, device = device).unsqueeze(1)).view(-1) #[batchsize * ntriangles * 3]
        neighbouring_edge = edges.masked_select(removed_edge_mask)
        neighbouring_edge_mask = torch.zeros([self.batchsize * self.ntriangles * 3], device = device, dtype = torch.bool)
        neighbouring_edge_mask[neighbouring_edge] = True
        neighbouring_edge_mask = (neighbouring_edge_mask * removed_edge_mask.logical_not()) #[batchsize * ntriangles * 3]
        
        n_new_triangles = neighbouring_edge_mask.view(self.batchsize, -1).sum(-1) #[batchsize]
        
        new_point = point_index.unsqueeze(1).expand(-1, self.ntriangles * 3).masked_select(neighbouring_edge_mask.view(self.batchsize, -1))
        
        second_point_mask = neighbouring_edge_mask.view(self.batchsize, -1, 3) #[batchsize, ntriangles 3]
        (first_point_indices0, first_point_indices1, first_point_indices2) = second_point_mask.nonzero(as_tuple = True)
        first_point_indices2 = (first_point_indices2 != 2) * (first_point_indices2 + 1)
        
        first_point = self.partial_delaunay_triangles[first_point_indices0, first_point_indices1, first_point_indices2] #[?]
        second_point = self.partial_delaunay_triangles.masked_select(second_point_mask) #[?]
        
        new_triangles_mask = torch.cat([incircle_test, torch.ones([self.batchsize, 2], dtype = torch.bool, device = device)], dim = 1) #[batchsize, ntriangles + 2]
        
        new_neighbouring_edges = 3 * new_triangles_mask.nonzero(as_tuple = True)[1] #[?], 3* since is the 01 edge of new triangles (see later)
        self.partial_delaunay_edges.masked_scatter_(neighbouring_edge_mask.view(self.batchsize, -1), new_neighbouring_edges) #still [batchsize, ntriangles * 3] for now
        
        self.partial_delaunay_triangles = torch.cat([self.partial_delaunay_triangles, torch.empty([self.batchsize, 2, 3], dtype = torch.long, device = device)], dim = 1)
        self.partial_delaunay_edges = torch.cat([self.partial_delaunay_edges, torch.empty([self.batchsize, 6], dtype = torch.long, device = device)], dim = 1)
        new_triangles = torch.stack([first_point, second_point, new_point], dim = 1) #[?, 3], edge here is flipped compared to edge in neighbouring triangle (so first_point is the second point in neighbouring edge)
        self.partial_delaunay_triangles.masked_scatter_(new_triangles_mask.unsqueeze(2).expand(-1, -1, 3), new_triangles) #[batchsize, ntriangles + 2, 3]
        
        new_edge01 = neighbouring_edge_mask.view(self.batchsize, -1).nonzero(as_tuple = True)[1] #[?]
        
        """we are currently storing which triangles have to be inserted, via the edges along the perimeter of the delaunay cavity, we need to compute which edge is to the 'left'/'right' of each edge"""
        """don't have the memory to do a batchsize * n * n boolean search, don't have the speed to do a batchsize^2 search (as would be the case for sparse matrix or similar)"""
        """best alternative: rotate the edge around right point, repeat until hit edge in mask (will never go to an edge of a removed triangle before we hit edge in mask) should basically be order 1!!!!!"""
        
        neighbouring_edge_index = neighbouring_edge_mask.nonzero(as_tuple = True)[0] #[?]
        next_neighbouring_edge_index = torch.empty_like(neighbouring_edge_index) #[?]
        
        rotating_flipped_neighbouring_edge_index = neighbouring_edge_mask.nonzero(as_tuple = True)[0] #[?], initialise
        todo_mask = torch.ones_like(next_neighbouring_edge_index, dtype = torch.bool) #[?]
        while todo_mask.sum():
            rotating_neighbouring_edge_index = rotating_flipped_neighbouring_edge_index + 1 - 3 * (rotating_flipped_neighbouring_edge_index % 3 == 2) #[todo_mask.sum()], gets smaller until nothing left EFFICIENCY (this may be seriously stupid, as it requires making a bunch of copies when I could be doing stuff inplace)
            
            update_mask = neighbouring_edge_mask[rotating_neighbouring_edge_index] #[todo_mask.sum()]
            update_mask_unravel = torch.zeros_like(todo_mask).masked_scatter(todo_mask, update_mask) #[?]
            
            next_neighbouring_edge_index.masked_scatter_(update_mask_unravel, rotating_neighbouring_edge_index.masked_select(update_mask)) #[?]
            
            todo_mask.masked_fill_(update_mask_unravel, False) #[?]
            rotating_flipped_neighbouring_edge_index = edges[rotating_neighbouring_edge_index.masked_select(update_mask.logical_not())] #[todo_mask.sum()]
        triangle_index = new_triangles_mask.view(-1).nonzero(as_tuple = True)[0] #[?], index goes up to batchsize * (ntriangles + 2), this is needed for when we invert the permutation by scattering (won't scatter same number of triangles per batch)
        
        next_triangle_index = torch.empty_like(edges).masked_scatter_(neighbouring_edge_mask, triangle_index)[next_neighbouring_edge_index] #[?], index goes up to batchsize * (ntriangles + 2)
        next_edge = 3 * next_triangle_index + 1 #[?]
        
        invert_permutation = torch.empty_like(new_triangles_mask.view(-1), dtype=torch.long) #[batchsize * (ntriangles + 2)]
        invert_permutation[next_triangle_index] = triangle_index #[batchsize * (ntriangles + 2)]
        previous_triangle_index = invert_permutation.masked_select(new_triangles_mask.view(-1)) #[?]
        previous_edge = 3 * previous_triangle_index + 2 #[?]
        
        """in the above we rotated around 'first_point' in our new triangles"""
        new_edge20 = next_edge % ((self.ntriangles + 2) * 3) #[?]
        new_edge12 = previous_edge % ((self.ntriangles + 2) * 3) #[?]
        
        new_edges = torch.stack([new_edge01, new_edge12, new_edge20], dim = 1) #[?, 3]
        self.partial_delaunay_edges.masked_scatter_(new_triangles_mask.unsqueeze(2).expand(-1, -1, 3).reshape(self.batchsize, -1), new_edges) #[batchsize, (ntriangles + 2) * 3]
        
        self.ntriangles += 2
        """currently only count the extra triangles you replace (not the on you have to remove because you're located there, and not the ones you make because you have to create two more"""
        self.cost += (n_new_triangles - 3)
        self.points_mask.scatter_(1, point_index.unsqueeze(1).expand(-1, self.npoints), True)
        self.points_sequence = torch.cat([self.points_sequence, point_index.unsqueeze(1)], dim = 1)
    
    def sample_point(self, logits): #logits must be [batchsize * nsamples, npoints]
        probs = torch.distributions.categorical.Categorical(logits = logits)
        next_point = probs.sample() #size is [batchsize * nsamples]
        self.update(next_point)
        self.logprob = self.logprob + probs.log_prob(next_point)
        return next_point #[batchsize * nsamples]
    
    def sampleandgreedy_point(self, logits): #logits must be [batchsize * nsamples, npoints], last sample will be the greedy choice (but we still need to keep track of its logits)
        logits_sample = logits.view(-1, self.nsamples, self.npoints)[:, :-1, :]
        probs = torch.distributions.categorical.Categorical(logits = logits_sample)
        
        sample_point = probs.sample() #[batchsize, (nsamples - 1)]
        greedy_point = logits.view(-1, self.nsamples, self.npoints)[:, -1, :].max(-1, keepdim = True)[1] #[batchsize, 1]
        next_point = torch.cat([sample_point, greedy_point], dim = 1).view(-1)
        self.update(next_point)
        self.logprob = self.logprob + torch.cat([probs.log_prob(sample_point), torch.zeros([sample_point.size(0), 1], device = device)], dim = 1).view(-1)
        return next_point
    

env = environment()


def train(epochs = 30000, npoints = 8, batchsize = 32, nsamples = 96):
    NN.train()
    for i in range(epochs):
        env.reset(npoints, batchsize, nsamples)
        """include the boundary points, kinda makes sense that they should contribute (atm only in the encoder, difficult to see how in the decoder)"""
        memory = NN.encode(env.points)
        #### #### #### remember to include tgt.detach() when reinstate with torch.no_grad()
        tgt = NN.start_token.unsqueeze(0).unsqueeze(1).expand(1, batchsize * nsamples, -1).detach()
        #with torch.no_grad(): #to speed up computation, selecting routes is done without gradient
        with torch.no_grad():
            for j in range(3, npoints):
                #### #### #### remember to include memory.detach() when reinstate with torch.no_grad()
                _, logits = NN.decode_next(memory.detach(), tgt, env.points_mask)
                next_point = env.sampleandgreedy_point(logits)
                """
                for inputing the previous embedding into decoder
                """
                tgt = torch.cat([tgt, memory.gather(0, next_point.unsqueeze(0).unsqueeze(2).expand(1, -1, memory.size(2)))])
                """
                for inputing the previous decoder output into the decoder (allows for an evolving strategy, but doesn't allow for fast training
                """
                ############

        
        _, logprob = NN.calculate_logprob(memory, env.points_sequence) #[batchsize * nsamples]
        """
        clip logprob so doesn't reinforce things it already knows
        TBH WANT SOMETHING DIFFERENT ... want to massively increase training if find something unexpected and otherwise not
        """
        greedy_baseline = env.cost.view(batchsize, nsamples)[:, -1] #[batchsize], greedy sample
        fixed_baseline = 0.5 * torch.ones([1], device = device)
        min_baseline = env.cost.view(batchsize, nsamples)[:, :-1].min(-1)[0] #[batchsize], minimum cost
        baseline = greedy_baseline
        positive_reinforcement = - F.relu( - (env.cost.view(batchsize, nsamples)[:, :-1] - baseline.unsqueeze(1))) #don't scale positive reinforcement
        negative_reinforcement = F.relu(env.cost.view(batchsize, nsamples)[:, :-1] - baseline.unsqueeze(1))
        positive_reinforcement_binary = env.cost.view(batchsize, nsamples)[:, :-1] - baseline.unsqueeze(1) <= 0
        negative_reinforcement_binary = env.cost.view(batchsize, nsamples)[:, :-1] - baseline.unsqueeze(1) > 0
        """
        binary positive reinforcement
        """
        #loss = - ((logprob.view(batchsize, nsamples)[:, :-1] < -0.2) * logprob.view(batchsize, nsamples)[:, :-1] * positive_reinforcement_binary).mean() #+ (logprob.view(batchsize, nsamples)[:, :-1] > -1) * logprob.view(batchsize, nsamples)[:, :-1] * negative_reinforcement_binary
        """
        clipped binary reinforcement
        """
        #loss = ( - logprob.view(batchsize, nsamples)[:, :-1] * (logprob.view(batchsize, nsamples)[:, :-1] < -0.2) * positive_reinforcement_binary + logprob.view(batchsize, nsamples)[:, :-1] * (logprob.view(batchsize, nsamples)[:, :-1] > -2) * negative_reinforcement_binary ).mean()
        """
        clipped binary postive, clipped weighted negative
        """
        #loss = ( - logprob.view(batchsize, nsamples)[:, :-1] * (logprob.view(batchsize, nsamples)[:, :-1] < -0.2) * positive_reinforcement_binary + logprob.view(batchsize, nsamples)[:, :-1] * (logprob.view(batchsize, nsamples)[:, :-1] > -2) * negative_reinforcement ).mean()
        """
        clipped reinforcement without rescaling
        """
        loss = ((logprob.view(batchsize, nsamples)[:, :-1] < -0.6) * logprob.view(batchsize, nsamples)[:, :-1] * positive_reinforcement + (logprob.view(batchsize, nsamples)[:, :-1] > -5) * logprob.view(batchsize, nsamples)[:, :-1] * negative_reinforcement).mean()
        """
        clipped reinforcement
        """
        #loss = (logprob.view(batchsize, nsamples)[:, :-1] * positive_reinforcement / (positive_reinforcement.var() + 0.001).sqrt() + (logprob.view(batchsize, nsamples)[:, :-1] > -3) * logprob.view(batchsize, nsamples)[:, :-1] * negative_reinforcement / (negative_reinforcement.var() + 0.001).sqrt()).mean()
        """
        balanced reinforcement
        """
        #loss = (logprob.view(batchsize, nsamples)[:, :-1] * (positive_reinforcement / (positive_reinforcement.var() + 0.001).sqrt() + negative_reinforcement / (negative_reinforcement.var() + 0.001).sqrt())).mean()
        """
        regular loss
        """
        #loss = (logprob.view(batchsize, nsamples)[:, :-1] * (positive_reinforcement + negative_reinforcement)).mean()
        optimizer.zero_grad()
        loss.backward()
        #print(NN.encoder.weight.grad)
        optimizer.step()
        #print(greedy_baseline.mean().item())
        print(greedy_baseline.mean().item(), logprob.view(batchsize, nsamples)[:, -1].mean().item(), logprob.view(batchsize, nsamples)[:, :-1].mean().item(), logprob[0].item(), env.logprob[0].item())

In [2]:
train() #no tanh, just clip learning STABLEISH (can normally recover...)
"""
DOES PICK SOME -200 logit routes... must be some floating point errors (use fp64?)
"""

-1.8204978704452515 -1.8204978704452515


RuntimeError: Negation, the `-` operator, on a bool tensor is not supported. If you are trying to invert a mask, use the `~` or `logical_not()` operator instead.

In [ ]:
train() #bigger transformer, some dropout, clip = -2 (seems more stable...)

1.28125 -1.7896249294281006
1.34375 -1.7482506036758423
1.03125 -1.4823626279830933
1.03125 -0.9624723196029663
1.03125 -1.1167057752609253
0.71875 -0.9132466912269592
0.96875 -0.7011247873306274
1.0 -0.6668125987052917
1.09375 -0.6439155340194702
1.0625 -0.46128547191619873
1.0625 -0.4960838854312897
1.0625 -0.3803693652153015
0.8125 -0.4132665693759918
1.0625 -0.37733107805252075
1.0 -0.3014765977859497
1.125 -0.34964460134506226
0.875 -0.4897526800632477
1.0625 -0.3763163387775421
1.09375 -0.31723645329475403
0.96875 -0.45358288288116455
1.09375 -0.31250569224357605
1.0625 -0.2369677573442459
0.875 -0.30709177255630493
1.1875 -0.18042482435703278
1.03125 -0.2228589653968811
1.0625 -0.2891862988471985
0.96875 -0.32585012912750244
1.0 -0.2987358570098877
1.125 -0.2869742512702942
1.0625 -0.27074676752090454
1.0625 -0.2956414222717285
1.0 -0.32417237758636475
0.96875 -0.27925828099250793
0.90625 -0.2422630488872528
1.09375 -0.2613318860530853
1.0 -0.1805688589811325
1.03125 -0.33196330

0.78125 -0.0878530889749527
1.03125 -0.07148400694131851
1.0625 -0.10774770379066467
1.15625 -0.06763865053653717
0.90625 -0.04989629238843918
1.0 -0.0317910760641098
1.0 -0.02925880253314972
0.96875 -0.05836367979645729
0.96875 -0.05661333352327347
1.0625 -0.04209968447685242
1.15625 -0.04029297083616257
0.90625 -0.07076127827167511
0.96875 -0.0330684594810009
1.0 -0.060455676168203354
1.0 -0.03782004863023758
1.15625 -0.025203166529536247
0.90625 -0.059367336332798004
0.90625 -0.037795908749103546
0.84375 -0.007698983885347843
0.84375 -0.0345761738717556
0.9375 -0.04186161234974861
0.78125 -0.035773515701293945
1.0 -0.06442174315452576
0.8125 -0.033654920756816864
0.9375 -0.04074482247233391
0.8125 -0.038880813866853714
0.84375 -0.011392341926693916
0.9375 -0.03983614593744278
0.65625 -0.04678601026535034
0.84375 -0.043370187282562256
1.09375 -0.04023507237434387
0.6875 -0.03855045139789581
0.9375 -0.04199353605508804
1.0 -0.04322186857461929
0.9375 -0.056342728435993195
0.875 -0.051

0.8125 -0.03379904851317406
1.0625 -0.0807044580578804
0.8125 -0.05341677367687225
1.375 -0.09176910668611526
0.90625 -0.07679541409015656
1.1875 -0.07193253934383392
1.03125 -0.08030454814434052
0.9375 -0.05992051586508751
1.15625 -0.07191978394985199
1.0625 -0.04760031774640083
1.0625 -0.015035782940685749
1.03125 -0.02016667276620865
0.90625 -0.04390818253159523
0.96875 -0.0458928644657135
0.65625 -0.03600573167204857
0.8125 -0.0558670312166214
0.875 -0.04350842162966728
1.0 -0.07924908399581909
0.78125 -0.04126153513789177
0.96875 -0.060627780854701996
0.84375 -0.06322255730628967
0.9375 -0.05486512556672096
1.09375 -0.032821815460920334
0.96875 -0.046112243086099625
1.0 -0.023819826543331146
0.65625 -0.050699591636657715
1.09375 -0.04070976376533508
0.75 -0.03753644973039627
1.09375 -0.027101509273052216
0.84375 -0.04946893826127052
0.875 -0.03753122687339783
1.0625 -0.021607648581266403
1.0 -0.04934869706630707
0.96875 -0.033262044191360474
0.84375 -0.019734377041459084
0.96875 -

In [ ]:
train() #same as above, but clip = -1.3

2.09375 -1.7896056175231934
1.375 -1.786285638809204
1.09375 -1.7267237901687622
1.125 -1.4259778261184692
1.09375 -0.9059238433837891
0.96875 -0.8897256851196289
1.03125 -0.5902172327041626
0.90625 -0.7056831121444702
0.8125 -0.5497967004776001
1.0 -0.5260083675384521
1.3125 -0.4182913899421692
1.0 -0.5615912675857544
0.96875 -0.4371412992477417
1.03125 -0.3702697455883026
0.875 -0.389050155878067
1.15625 -0.26530393958091736
0.84375 -0.36980316042900085
1.0625 -0.4767768383026123
0.9375 -0.4835342764854431
0.9375 -0.36496859788894653
1.03125 -0.21983879804611206
0.8125 -0.23969298601150513
1.28125 -0.28070056438446045
0.90625 -0.3242540955543518
1.0625 -0.28815174102783203
0.84375 -0.24599093198776245
0.78125 -0.30335336923599243
0.96875 -0.24776627123355865
0.71875 -0.19036555290222168
0.9375 -0.2761586308479309
1.0625 -0.15308022499084473
0.8125 -0.11776641756296158
0.875 -0.14321193099021912
1.09375 -0.1371580958366394
1.0625 -0.10710787773132324
0.8125 -0.20193922519683838
0.75 -

1.0 -0.022268319502472878
0.96875 -0.020763659849762917
1.03125 -0.026117457076907158
0.96875 -0.03242789953947067
0.9375 -0.01657894067466259
0.875 -0.04227776452898979
0.90625 -0.03322110325098038
0.78125 -0.02474590763449669
0.9375 -0.023854419589042664
1.0 -0.057480357587337494
1.1875 -0.03413807600736618
0.875 -0.025458600372076035
0.84375 -0.05300555378198624
0.96875 -0.04033603519201279
1.09375 -0.04231848567724228
0.8125 -0.1073661670088768
1.0 -0.030045021325349808
0.84375 -0.0372752770781517
0.8125 -0.05219388008117676
0.875 -0.03711890056729317
0.84375 -0.014456315897405148
0.84375 -0.04649141803383827
0.8125 -0.024923376739025116
0.75 -0.020466264337301254
0.9375 -0.034594032913446426
0.90625 -0.015088213607668877
0.90625 -0.00874014850705862
0.9375 -0.032289598137140274
1.0625 -0.02143404260277748
1.09375 -0.030328214168548584
0.875 -0.03161287680268288
1.0 -0.029102351516485214
1.09375 -0.017907576635479927
0.8125 -0.014164706692099571
0.96875 -0.008893890306353569
0.875 

0.9375 -0.026160456240177155
1.03125 -0.023846406489610672
0.71875 -0.05824717879295349
1.09375 -0.03897411376237869
1.21875 -0.0496969148516655
0.96875 -0.04919206723570824
0.9375 -0.06642022728919983
1.0625 -0.08731552958488464
1.03125 -0.04052473604679108
0.84375 -0.03302743285894394
1.0625 -0.040173739194869995
0.84375 -0.03335615620017052
1.15625 -0.039893992245197296
0.90625 -0.02909437194466591
1.03125 -0.044767461717128754
0.96875 -0.02337525598704815
1.09375 -0.04615389183163643
0.96875 -0.027439583092927933
1.03125 -0.04335799813270569
0.875 -0.030696241185069084
0.8125 -0.04614952206611633
0.84375 -0.0322859063744545
0.96875 -0.018381979316473007
0.9375 -0.008006401360034943
1.0 -0.018706507980823517
1.0625 -0.021250678226351738
0.9375 -0.03373710811138153
1.03125 -0.00960100069642067
1.125 -0.016263924539089203
0.875 -0.04168430715799332
1.03125 -0.056864652782678604
0.84375 -0.07119506597518921
0.875 -0.013310771435499191
0.90625 -0.02968260832130909
1.0 -0.020742582157254

0.96875 -0.013072317466139793
0.9375 -0.013871511444449425
0.9375 -0.008340765722095966
0.90625 -0.011164880357682705
1.09375 -0.004411877132952213
0.96875 -0.011514037847518921
1.0 -0.018102120608091354
0.96875 -0.008604014292359352
0.84375 -0.0157743189483881
0.875 -0.005189666990190744
0.90625 -0.007994171231985092
1.0 -0.009119249880313873
0.625 -0.003798023797571659
0.84375 -0.012095327489078045
1.0 -0.005286672152578831
1.0 -0.00891290046274662
0.96875 -0.010860196314752102
1.09375 -0.012786691077053547
0.875 -0.014524463564157486
0.9375 -0.03037259355187416
1.0625 -0.04454538971185684
1.28125 -0.0789729654788971
1.25 -0.04559437558054924
1.0625 -0.016898732632398605
1.1875 -0.039986684918403625
0.8125 -0.03255854547023773
1.03125 -0.020977791398763657
0.75 -0.027989517897367477
0.84375 -0.035705216228961945
0.84375 -0.029665952548384666
0.875 -0.03814275562763214
1.15625 -0.04827006161212921
1.0625 -0.05531010776758194
1.125 -0.035485461354255676
1.09375 -0.028729574754834175
0.

1.09375 -0.01068113837391138
0.75 -0.010777156800031662
0.9375 -0.010882195085287094
0.9375 -0.01575356349349022
1.09375 -0.017094066366553307
0.9375 -0.013496938161551952
1.0625 -0.007268979214131832
0.875 -0.02708391100168228
0.75 -0.004688226617872715
0.875 -0.013480943627655506
1.125 -0.01734585501253605
0.96875 -0.027002647519111633
1.125 -0.010386781767010689
0.96875 -0.015443304553627968
0.8125 -0.009647920727729797
1.0 -0.026433710008859634
0.90625 -0.014265121892094612
0.84375 -0.020160973072052002
0.6875 -0.029472745954990387
0.90625 -0.006308451294898987
0.84375 -0.030299965292215347
0.875 -0.022344304248690605
0.9375 -0.016672737896442413
0.78125 -0.009065324440598488
1.09375 -0.014972364529967308
1.03125 -0.007655204739421606
0.90625 -0.005221976432949305
1.125 -0.020566735416650772
0.90625 -0.019603373482823372
0.9375 -0.0056817675940692425
0.625 -0.009144296869635582
0.65625 -0.0061900001019239426
0.84375 -0.011164939031004906
0.78125 -0.017728619277477264
1.0 -0.0175327

0.75 -0.013979572802782059


In [ ]:
train() #more logging to see what's happening

1.46875 -1.7039947509765625 -1.7895152568817139
0.9375 -1.562101125717163 -1.7711296081542969
0.90625 -1.1866734027862549 -1.6309475898742676
0.875 -0.6566133499145508 -1.104162573814392
0.84375 -0.44229868054389954 -0.788345217704773
0.96875 -0.4910595417022705 -0.7979297637939453
1.0625 -0.35269635915756226 -0.6038947105407715
1.03125 -0.27578210830688477 -0.5021243691444397
1.09375 -0.276239275932312 -0.52205491065979
0.78125 -0.33817529678344727 -0.6147326827049255
1.0 -0.1950552761554718 -0.47660183906555176
1.09375 -0.17968907952308655 -0.3968462347984314
0.9375 -0.3402549624443054 -0.4986550211906433
1.0 -0.3564119338989258 -0.5254104733467102
0.71875 -0.28254449367523193 -0.4235957860946655
1.0625 -0.2330329716205597 -0.3996066451072693
0.75 -0.19702276587486267 -0.3674478232860565
0.9375 -0.1809324026107788 -0.3523162305355072
1.1875 -0.21306169033050537 -0.4028622508049011
0.8125 -0.19277110695838928 -0.3548511862754822
1.0 -0.25723886489868164 -0.4519727826118469
1.0 -0.2870

0.8125 -0.03526739776134491 -0.08609142154455185
0.78125 -0.0515868254005909 -0.06832913309335709
1.0625 -0.03644032031297684 -0.08654307574033737
0.90625 -0.043295085430145264 -0.08145295828580856
0.9375 -0.0044255852699279785 -0.033389460295438766
0.78125 -0.03998042270541191 -0.05193593353033066
1.03125 -0.03010459616780281 -0.027965813875198364
0.84375 -0.02194887399673462 -0.03147304058074951
0.875 -0.02619008719921112 -0.031161030754446983
0.84375 -0.049872756004333496 -0.07402653992176056
1.0625 -0.031103238463401794 -0.06597524881362915
1.0 -0.033250078558921814 -0.07806934416294098
0.9375 -0.006106957793235779 -0.037529356777668
0.875 -0.013782128691673279 -0.05376821383833885
1.09375 -0.012841761112213135 -0.05835730582475662
1.0 -0.003502778708934784 -0.023444607853889465
1.0625 -0.03913665562868118 -0.05914641544222832
0.875 -0.005740884691476822 -0.07451194524765015
0.8125 -0.034726377576589584 -0.07636964321136475
1.125 -0.020920120179653168 -0.09598427265882492
1.03125 -

0.84375 -0.018479004502296448 -0.025851905345916748
0.84375 -0.0016289353370666504 -0.027915459126234055
0.9375 -0.004312440752983093 -0.03437117859721184
0.8125 -0.009279254823923111 -0.022452715784311295
0.8125 -0.0022466182708740234 -0.016330284997820854
1.09375 -0.008524611592292786 -0.02296161651611328
1.21875 -0.04781666398048401 -0.04730778932571411
1.0 -0.0225803442299366 -0.03141945227980614
0.90625 -0.015720993280410767 -0.0314771868288517
1.125 -0.016034595668315887 -0.040305957198143005
0.84375 -0.009523779153823853 -0.024732057005167007
1.0625 -0.03386125713586807 -0.04501957446336746
1.0 -0.011577427387237549 -0.07170214504003525
0.8125 -0.0007876716554164886 -0.016505632549524307
0.6875 -0.023514464497566223 -0.02805926278233528
0.9375 -0.02018594555556774 -0.03586103394627571
1.09375 -0.02388019859790802 -0.04963400214910507
0.90625 -0.012937627732753754 -0.03533574193716049
1.03125 -0.008540600538253784 -0.02008809894323349
0.96875 -0.03796207904815674 -0.0385022126138

0.96875 -0.015375358983874321 -0.02906010113656521
0.875 -0.004979550838470459 -0.025307556614279747
0.65625 -0.014546994119882584 -0.04147319495677948
1.21875 -0.00846630334854126 -0.044188112020492554
1.03125 -0.011253595352172852 -0.03986288234591484
0.96875 -0.001658618450164795 -0.024183280766010284
0.8125 -0.02247387170791626 -0.03764178976416588
1.0625 -0.023521967232227325 -0.06059103459119797
0.8125 -0.006900787353515625 -0.019997432827949524
0.8125 -0.01576375961303711 -0.021465545520186424
0.96875 -0.04695643484592438 -0.06460101902484894
1.0 -0.0010386332869529724 -0.030876141041517258
0.96875 -0.003282099962234497 -0.024487510323524475
0.65625 -0.02341601252555847 -0.05531593784689903
0.90625 -0.024715781211853027 -0.030979584902524948
0.9375 -0.004212617874145508 -0.03381332755088806
0.90625 -0.02393639087677002 -0.041613608598709106
0.96875 -0.02040836215019226 -0.040807079523801804
1.03125 -0.04052048921585083 -0.04158894717693329
0.90625 -0.0008274763822555542 -0.03510

0.96875 -0.0045327842235565186 -0.03641277924180031
0.96875 -0.012965917587280273 -0.010530378669500351
0.875 -0.005510449409484863 -0.026172270998358727
1.0625 -0.017807841300964355 -0.04611688479781151
0.84375 -0.036261945962905884 -0.04437587782740593
0.90625 -0.0013064518570899963 -0.05884590744972229
0.8125 -0.021053753793239594 -0.036725737154483795
0.71875 -0.009116411209106445 -0.02497059665620327
0.9375 -0.05665913224220276 -0.03825277462601662
0.96875 -0.0005098283290863037 -0.023949671536684036
0.78125 -0.02808159589767456 -0.025407060980796814
0.9375 -0.011096011847257614 -0.04062946140766144
1.09375 -0.023546934127807617 -0.027995627373456955
0.75 -0.0242459774017334 -0.03748192638158798
1.0625 -0.027565956115722656 -0.017339808866381645
0.8125 -0.021803736686706543 -0.009188929572701454
0.78125 -0.015608564019203186 -0.026121025905013084
0.875 -0.0018796920776367188 -0.023918040096759796
0.9375 -3.5762786865234375e-05 -0.01143641397356987
0.6875 -0.03537005931138992 -0.01

In [ ]:
train() #dropout = 0.1, clip = -0.5

1.59375 -1.6680917739868164 -1.785887598991394
1.34375 -1.3114981651306152 -1.685712218284607
1.15625 -0.9076878428459167 -1.349170207977295
1.28125 -0.68962562084198 -1.1179800033569336
1.03125 -0.6069835424423218 -0.9107990264892578
1.15625 -0.4892837405204773 -0.7900959849357605
0.8125 -0.5107496380805969 -0.7472376823425293
0.875 -0.33175545930862427 -0.604354977607727
1.125 -0.5109047889709473 -0.7808758616447449
0.9375 -0.49299246072769165 -0.7515493631362915
1.1875 -0.23360247910022736 -0.4288007616996765
1.0625 -0.3309866189956665 -0.519012451171875
1.03125 -0.2225417047739029 -0.48764607310295105
0.9375 -0.19748659431934357 -0.43414586782455444
1.1875 -0.3181260824203491 -0.4724884033203125
1.03125 -0.15946070849895477 -0.31287282705307007
1.0625 -0.17365683615207672 -0.3070104718208313
0.96875 -0.1771981120109558 -0.3053884208202362
0.9375 -0.2040363997220993 -0.35946282744407654
1.03125 -0.16323506832122803 -0.3131764829158783
1.21875 -0.22665876150131226 -0.3388662338256836

0.875 -0.010608233511447906 -0.06391635537147522
1.03125 -0.02867581695318222 -0.11234280467033386
0.90625 -0.03547666221857071 -0.06030651181936264
0.84375 -0.036077290773391724 -0.059590499848127365
1.1875 -0.019676297903060913 -0.06865525245666504
1.0 -0.016731660813093185 -0.08697885274887085
0.875 -0.05516240373253822 -0.07136192917823792
0.875 -0.04336804151535034 -0.06374941766262054
1.03125 -0.06462130695581436 -0.09776583313941956
1.0625 -0.041404351592063904 -0.090442955493927
1.03125 -0.05233563482761383 -0.08585046231746674
0.71875 -0.0010980274528265 -0.033012207597494125
0.71875 -0.04310399293899536 -0.10542687028646469
1.03125 -0.04668086767196655 -0.09703793376684189
1.0 -0.06882433593273163 -0.08937911689281464
0.84375 -0.033778026700019836 -0.09443643689155579
0.90625 -0.03921575844287872 -0.12226396799087524
0.9375 -0.04914828762412071 -0.07496118545532227
1.15625 -0.07162877917289734 -0.07438333332538605
0.875 -0.03916269540786743 -0.06052204966545105
1.15625 -0.021

0.96875 -0.03178972005844116 -0.08711826056241989
1.125 -0.027978375554084778 -0.07069283723831177
1.09375 -0.02663145214319229 -0.06086701154708862
0.90625 -0.0033415518701076508 -0.0548131987452507
1.0625 -0.040326379239559174 -0.06247888132929802
1.03125 -0.015162141993641853 -0.058158814907073975
0.96875 -0.03689113259315491 -0.05225948616862297
1.125 -0.035514697432518005 -0.056785017251968384
1.0 -0.04184447228908539 -0.0782097578048706
0.875 -0.028909601271152496 -0.06587521731853485
1.21875 -0.03385469317436218 -0.0336601547896862
0.84375 -0.07214511930942535 -0.07377373427152634
0.875 -0.038851335644721985 -0.03534328192472458
1.03125 -0.013109572231769562 -0.028280988335609436
0.9375 -0.013905514031648636 -0.04107937216758728
1.03125 -0.007946453988552094 -0.03416530042886734
1.0625 -0.009891003370285034 -0.0661897361278534
1.03125 -0.05851007252931595 -0.030498962849378586
0.96875 -0.02652987837791443 -0.055790286511182785
1.0 -0.018996119499206543 -0.038176529109478
1.28125

0.9375 -0.018907785415649414 -0.03188716620206833
1.0 -0.006225228309631348 -0.03028678148984909
1.03125 -0.00811755657196045 -0.017394067719578743
0.78125 -0.006156839430332184 -0.04364227503538132
0.90625 -0.006015658378601074 -0.043815769255161285
1.0 -0.05144810676574707 -0.04520772024989128
0.84375 -0.027867693454027176 -0.03298328444361687
0.875 -0.015615463256835938 -0.023303311318159103
1.09375 -0.024581700563430786 -0.03677491843700409
0.875 -0.024810485541820526 -0.03986284136772156
0.78125 -0.0027016177773475647 -0.03413867577910423
0.875 -0.025607507675886154 -0.0506533607840538
0.90625 -0.03320060670375824 -0.026219835504889488
1.03125 -0.018110055476427078 -0.04543270915746689
1.03125 -0.05633437633514404 -0.04101686179637909
1.0625 -0.02854917198419571 -0.032166630029678345
0.875 -0.014234498143196106 -0.025077668949961662
1.03125 -0.009124979376792908 -0.0308066513389349
1.0 -0.003994673490524292 -0.030071435496211052
0.75 -0.012191548943519592 -0.029074322432279587
1.0

0.8125 -0.008625486865639687 -0.036960169672966
0.8125 -0.011429429054260254 -0.02697119116783142
1.03125 -0.021510422229766846 -0.04082009941339493
1.0625 -0.020599879324436188 -0.026425277814269066
0.96875 -0.035503923892974854 -0.03880397975444794
1.03125 -0.016773145645856857 -0.05220529064536095
0.90625 -0.014740914106369019 -0.0421736016869545
1.1875 -0.00669628381729126 -0.04519939422607422
0.96875 -0.04800644516944885 -0.061979442834854126
0.8125 -0.03870710730552673 -0.07013949751853943
1.0 -0.03338855504989624 -0.06300953030586243
0.90625 -0.002200186252593994 -0.07409872114658356
1.0 -0.08106434345245361 -0.05401591584086418
1.03125 -0.00559389591217041 -0.04197731614112854
0.90625 -0.024744629859924316 -0.03761964291334152
0.75 -0.01792430877685547 -0.0464642159640789
1.09375 -0.03935122489929199 -0.03498055040836334
0.9375 -0.020911335945129395 -0.029487352818250656
0.9375 -0.015725061297416687 -0.05120830982923508
0.8125 -0.0019971132278442383 -0.01519766729325056
1.03125

...

1.0625 -0.0302736759185791 -0.03562527522444725
1.15625 -0.027030721306800842 -0.029024949297308922
1.03125 -0.009909149259328842 -0.024625107645988464
0.90625 -0.0028892457485198975 -0.020325906574726105
1.1875 -0.0012244582176208496 -0.026984548196196556
1.09375 -0.027985870838165283 -0.047583457082509995
1.125 -0.004383742809295654 -0.033007413148880005
0.75 -0.02276521921157837 -0.03235718980431557
1.0 -0.00046706199645996094 -0.03097604773938656
1.0625 -0.016735553741455078 -0.03906717151403427
1.25 -0.006081536412239075 -0.022592488676309586
0.6875 -0.04258322715759277 -0.020699381828308105
1.125 -0.011632978916168213 -0.03866022080183029
1.09375 -0.002369508147239685 -0.022322900593280792
0.9375 -0.020735546946525574 -0.02541196346282959
0.90625 -0.020614072680473328 -0.016074445098638535
0.96875 -0.014747999608516693 -0.02795330435037613
1.09375 -0.057059288024902344 -0.025037601590156555
1.125 -0.01745373010635376 -0.043131813406944275
0.8125 -0.049402326345443726 -0.026783354

1.0625 -0.002544403076171875 -0.020015466958284378
1.0625 -0.005774140357971191 -0.017874745652079582
1.09375 -0.03151458501815796 -0.023072298616170883
0.78125 -0.004674434661865234 -0.025552934035658836
0.96875 -2.9087066650390625e-05 -0.01511850580573082
1.28125 -0.015921950340270996 -0.022215811535716057
0.96875 -0.006651431322097778 -0.01741456240415573
1.1875 -0.008711248636245728 -0.021262919530272484
0.84375 -2.193450927734375e-05 -0.019068855792284012
0.875 -0.0028481483459472656 -0.01712968572974205
0.875 -0.014736950397491455 -0.02471417747437954
0.8125 -0.012082576751708984 -0.02893689274787903
1.21875 -4.76837158203125e-07 -0.017733070999383926
1.0625 -0.0008436441421508789 -0.019001906737685204
1.21875 -0.0038147717714309692 -0.023246794939041138
0.75 -0.01871776580810547 -0.016991926357150078
0.96875 -4.00543212890625e-05 -0.015196369960904121
0.9375 -0.03856205940246582 -0.025128986686468124
0.96875 -0.0038590431213378906 -0.01299987267702818
1.03125 -8.0108642578125e-0

1.0 -0.0006685517728328705 -0.0169710423797369
1.0625 -0.0002529025077819824 -0.014679688028991222
0.9375 -2.384185791015625e-05 -0.01999620348215103
1.125 -0.00015294551849365234 -0.017918337136507034
0.9375 -0.0001977682113647461 -0.020240452140569687
1.03125 -0.0004905462265014648 -0.016071606427431107
1.0625 -0.01258540153503418 -0.022593265399336815
1.0 -0.001677870750427246 -0.011153253726661205
0.75 -0.027002930641174316 -0.011760375462472439
0.96875 -9.173154830932617e-05 -0.01216701976954937
0.8125 -0.003407597541809082 -0.009891046211123466
0.90625 -0.0005984306335449219 -0.01641027443110943
1.03125 -0.017693400382995605 -0.011796524748206139
0.9375 -0.00328807532787323 -0.018896259367465973
0.6875 -4.76837158203125e-07 -0.012288806959986687
1.125 -0.004519402980804443 -0.019243624061346054
0.90625 -0.0008910894393920898 -0.01784059964120388
0.875 -0.0011886358261108398 -0.021353691816329956
0.75 -0.0002129077911376953 -0.02008720301091671
1.0 -3.337860107421875e-06 -0.017706

0.90625 -0.01646900177001953 -0.011349464766681194
0.96875 -0.00023790448904037476 -0.006273123901337385
0.84375 -0.002689540386199951 -0.009496286511421204
0.875 -0.011064503341913223 -0.01622600480914116
0.9375 -0.00014100223779678345 -0.0223061665892601
1.03125 -0.0007827281951904297 -0.008354220539331436
1.0 -0.015488982200622559 -0.010133270174264908
1.0625 -0.000558316707611084 -0.01170117687433958
1.03125 -0.014348864555358887 -0.014092701487243176
1.03125 -0.0005394518375396729 -0.022256826981902122
1.09375 -0.0003795623779296875 -0.012245400808751583
1.0625 -0.012281492352485657 -0.015026917681097984
1.0 -6.341934204101562e-05 -0.005532383918762207
1.125 -0.008329890668392181 -0.016919389367103577
0.96875 -0.013332292437553406 -0.022033847868442535
1.0 -0.0003106445074081421 -0.02249520644545555
1.09375 -0.001660853624343872 -0.023073673248291016
1.125 -0.00011867284774780273 -0.025121401995420456
0.9375 -5.960464477539063e-08 -0.010779491625726223
1.09375 -0.02102440595626831

1.0625 -0.010530471801757812 -0.019710306078195572
0.875 -0.002002239227294922 -0.02501228265464306
0.90625 -0.0335349440574646 -0.026842903345823288
0.90625 -0.00033690035343170166 -0.010021574795246124
0.8125 -0.0018053054809570312 -0.0219799242913723
1.03125 -0.011576533317565918 -0.010921514593064785
1.1875 -0.013640165328979492 -0.023565983399748802
0.90625 -0.020168066024780273 -0.011264431290328503
0.8125 -0.00981128215789795 -0.016555726528167725
1.03125 -0.02675342559814453 -0.016466576606035233
1.0625 -0.0016632080078125 -0.016426488757133484
0.75 -0.001989901065826416 -0.015352646820247173
0.96875 -0.0008102171123027802 -0.012076485902071
0.9375 -0.0006902217864990234 -0.019856013357639313
1.15625 -0.008849620819091797 -0.014712694101035595
0.9375 -0.025126099586486816 -0.02834821306169033
0.96875 -0.0015248209238052368 -0.017348840832710266
0.75 -0.004804283380508423 -0.02568472921848297
0.96875 -0.0017470195889472961 -0.021860171109437943
1.03125 -0.016476061195135117 -0.0

In [ ]:
train() #use minimum cost, not greedy (and clip = -2), AND positive reinforcement always has weight 1
"""
shouldn't be possible to have probabilities this low
"""

1.46875 -1.7265442609786987 -1.7879081964492798
1.15625 -1.4855763912200928 -1.762926697731018
1.3125 -1.0769803524017334 -1.5593420267105103
0.9375 -0.779782772064209 -1.2264989614486694
1.15625 -0.5418553352355957 -0.9897152781486511
0.9375 -0.7473282814025879 -1.1512223482131958
1.0 -0.8066710233688354 -1.2453464269638062
1.03125 -1.8787763118743896 -2.000370740890503
1.1875 -0.9565660953521729 -1.0968468189239502
1.21875 -0.7696458101272583 -1.222853660583496
1.0625 -2.3880269527435303 -2.820162296295166
1.21875 -4.720955848693848 -5.278475284576416
1.03125 -5.97210168838501 -6.190074443817139
1.28125 -6.125969886779785 -5.865928649902344
1.3125 -2.070702075958252 -3.822922468185425
1.28125 -3.1314148902893066 -4.300122261047363
1.28125 -3.728426933288574 -3.3728015422821045
1.3125 -8.912124633789062 -8.886573791503906
1.21875 -10.752815246582031 -10.639947891235352
1.5 -6.498696804046631 -6.781457901000977
1.4375 -16.56180763244629 -16.130617141723633
1.40625 -15.447624206542969 -

1.28125 -21190.623046875 -21329.3671875
1.4375 -22987.703125 -22505.330078125
1.28125 -20975.33203125 -23147.40625
1.34375 -22748.138671875 -23012.330078125
1.21875 -23710.955078125 -23639.896484375
1.375 -24703.5234375 -24951.3359375
1.34375 -24529.0703125 -24579.361328125
1.1875 -25869.484375 -25420.24609375
1.4375 -26210.28515625 -26293.24609375
1.40625 -27194.21484375 -26833.529296875
1.0625 -27699.86328125 -27197.912109375
1.5625 -26864.28125 -26887.880859375
1.46875 -25990.634765625 -26561.484375
1.40625 -22043.59375 -25906.1015625
1.1875 -23711.1328125 -24849.8984375
1.3125 -25366.91015625 -22164.400390625
1.40625 -19473.97265625 -19405.568359375
1.28125 -21090.185546875 -22166.353515625
1.53125 -27006.27734375 -27764.28515625
1.25 -30969.212890625 -30467.482421875
1.125 -29025.41015625 -29444.0390625
1.34375 -30906.76953125 -31208.798828125
1.34375 -31456.755859375 -30376.775390625
1.34375 -31934.953125 -31743.482421875
1.09375 -31637.947265625 -31268.0859375
1.25 -32668.726562

In [ ]:
train() #debug above
"""
env.logprob disagrees with decoder logprob
"""

-1.8153417110443115 -1.8752086162567139
1.375 -1.6919883489608765 -1.7895399332046509
-1.4157556295394897 -1.3717193603515625
1.5 -1.4357640743255615 -1.7510628700256348
-1.6872471570968628 -1.6740293502807617
1.09375 -1.3902671337127686 -1.712149977684021
-0.8119931221008301 -0.8480983972549438
1.15625 -0.9172778725624084 -1.396828293800354
-1.6225004196166992 -1.832794427871704
1.21875 -1.150543212890625 -1.5419890880584717
-0.5722143650054932 -0.8782798051834106
0.90625 -1.5445709228515625 -1.9002585411071777
-5.000434875488281 -2.7584586143493652
1.5 -2.0463194847106934 -2.5830881595611572
-4.182048797607422 -1.7174502611160278
1.03125 -2.5936203002929688 -2.8736302852630615
-5.012325286865234 -0.6356465816497803
1.25 -2.3483572006225586 -3.095632791519165
-2.054598331451416 -2.13226318359375
1.46875 -1.52437424659729 -1.6668663024902344
-0.22618317604064941 -0.6825525164604187
1.59375 -3.0530500411987305 -3.6400949954986572
-0.923703670501709 -0.7358098030090332
1.5625 -4.38175964

-3482.103271484375 -0.00311279296875
1.125 -3473.81005859375 -3435.087646484375
-3649.05908203125 -0.4754638671875
1.46875 -3557.5009765625 -3583.144775390625
-1939.517578125 0.0
1.28125 -3614.40087890625 -3711.3837890625
-3817.71240234375 0.0
1.03125 -3824.547119140625 -3793.873291015625
-3925.5322265625 0.0
1.53125 -3995.99072265625 -3932.675048828125
-4075.85693359375 -1.38800048828125
1.375 -3946.9765625 -3994.953857421875
-4084.36865234375 -0.00067138671875
1.3125 -4236.8544921875 -4086.77978515625
-4283.322265625 -1.13909912109375
1.0 -4237.0146484375 -4206.03759765625
-4392.5615234375 0.0
1.375 -4353.822265625 -4301.73486328125
-1.844482421875 -0.224609375
1.25 -4387.515625 -4414.39306640625
-4634.6181640625 -0.0609130859375
1.15625 -4567.09326171875 -4517.767578125
-4738.4287109375 -0.0101318359375
1.25 -4747.83203125 -4608.34619140625
-4846.916015625 -0.0010986328125
1.28125 -4676.66162109375 -4700.16015625
-4997.81640625 -0.657958984375
1.28125 -4925.6748046875 -4903.51025390

-37274.6953125 0.0
1.34375 -37286.28125 -37044.4921875
-37870.06640625 0.0
1.125 -37850.421875 -37690.390625
-38431.375 0.0
1.3125 -37871.35546875 -38239.3359375
-38899.875 0.0
1.3125 -38732.203125 -38742.67578125
-39457.71875 0.0
1.59375 -38844.69140625 -38692.0234375
-39844.9296875 0.0
1.1875 -39797.3984375 -39474.19921875
-40540.1796875 0.0
1.34375 -40438.2109375 -39947.80078125
-40599.8046875 0.0
1.34375 -40330.0546875 -40335.015625
-41339.28125 0.0
1.59375 -41347.96875 -40748.3125
-42007.90234375 0.0
1.0625 -41975.1484375 -41775.49609375
-42285.8984375 0.0
1.375 -42439.41015625 -42047.26953125
-43199.546875 0.0
1.1875 -43003.1875 -42794.6796875
-43331.9765625 0.0
1.40625 -43052.71875 -43454.95703125
-44180.9921875 0.0
1.25 -44123.66796875 -43856.2109375
-44759.265625 -0.3720703125
1.21875 -44714.28125 -44504.76171875
-45411.203125 0.0
1.25 -45193.6015625 -44573.6171875
-45736.53125 0.0
1.40625 -45854.8203125 -45275.359375
-46346.6796875 0.0
1.34375 -45001.8203125 -45891.98046875
-

0.0 0.0
1.625 0.0 -0.009187397547066212
0.0 0.0
1.5 -0.00537109375 -0.007745040580630302
0.0 0.0
1.21875 0.0 -0.006931666750460863
0.0 0.0
1.375 -0.02020263671875 -0.007072368636727333
0.0 0.0
1.46875 -0.0032958984375 -0.006037662271410227
0.0 0.0
1.5 -0.018798828125 -0.010048956610262394
0.0 0.0
1.53125 -0.03863525390625 -0.009041556157171726
0.0 0.0
1.28125 -0.0001220703125 -0.015326570719480515
0.0 0.0
1.40625 -0.00299072265625 -0.010971230454742908
0.0 0.0
1.375 -0.01300048828125 -0.007678222842514515
-0.001953125 -0.001953125
1.46875 -0.003936767578125 -0.013048995286226273
0.0 0.0
1.34375 0.0 -0.1362660974264145
0.0 0.0
1.53125 -0.00079345703125 -0.011118879541754723
0.0 0.0
1.3125 -0.001708984375 -0.0094836987555027
0.0 0.0
1.34375 -0.001953125 -0.09956472367048264
0.0 0.0
1.4375 -0.0020751953125 -0.016605699434876442
-2.625 -2.1455078125
1.28125 -0.016815185546875 -0.009754382073879242
0.0 0.0
1.59375 -0.00030517578125 -0.007327110040932894
0.0 0.0
1.625 0.0 -0.0076345345005393

0.0 0.0
1.5625 0.0 -0.005457185674458742
0.0 0.0
1.78125 0.0 -0.003162263659760356
0.0 0.0
1.28125 -0.0001220703125 -0.004645096603780985
0.0 0.0
1.3125 -0.001708984375 -0.0036338407080620527
0.0 0.0
1.53125 -0.017822265625 -0.0047350432723760605
0.0 0.0
1.5 0.0 -0.0035580284893512726
0.0 0.0
1.15625 -0.0115966796875 -0.004809570498764515
0.0 0.0
1.34375 0.0 -0.003155838930979371
0.0 0.0
1.40625 0.0 -0.005398077890276909
0.0 0.0
1.5 0.0 -0.005107678938657045
0.0 0.0
1.4375 0.0 -0.005622944328933954
0.0 0.0
1.46875 0.0 -0.005431486759334803
0.0 0.0
1.5 -0.0001220703125 -0.004553865175694227
0.0 0.0
1.5625 0.0 -0.005706466268748045
0.0 0.0
1.1875 -0.0003662109375 -0.004457494243979454
0.0 0.0
1.625 -0.0050048828125 -0.0051012542098760605
0.0 0.0
1.5 0.0 -0.003776470199227333
0.0 0.0
1.40625 -0.000244140625 -0.0036338407080620527
0.0 0.0
1.71875 0.0 -0.0024966592900455
0.0 0.0
1.5 -0.000732421875 -0.0027151007670909166
0.0 0.0
1.6875 0.0 -0.004786441568285227
0.0 0.0
1.34375 0.0 -0.003726

...

0.0 0.0
1.46875 -0.002685546875 -0.005760434083640575
0.0 0.0
1.3125 0.0 -0.005107678938657045
0.0 0.0
1.40625 -0.0001220703125 -0.0029027035925537348
0.0 0.0
1.125 -0.003173828125 -0.005954461637884378
0.0 0.0
1.59375 -0.000244140625 -0.004316149279475212
0.0 0.0
1.65625 0.0 -0.005527858156710863
0.0 0.0
1.5 0.0 -0.0034398131538182497
0.0 0.0
1.40625 0.0 -0.004263466689735651
0.0 0.0
1.4375 0.0 -0.004893092438578606
-4.29296875 -4.5
1.3125 0.0 -0.004493472632020712
0.0 0.0
1.28125 0.0 -0.006217876449227333
0.0 0.0
1.53125 -0.004150390625 -0.002346320077776909
0.0 0.0
1.3125 -0.001220703125 -0.005347964819520712
0.0 0.0
1.25 0.0 -0.005531712900847197
0.0 0.0
1.84375 0.0 -0.005932617466896772
0.0 0.0
1.25 -0.000244140625 -0.002506938762962818
0.0 0.0
1.46875 0.0 -0.005935187451541424
0.0 0.0
1.53125 0.0 -0.004323859233409166
0.0 0.0
1.28125 0.0 -0.0032265111804008484
0.0 0.0
1.53125 -0.0162353515625 -0.009675678797066212
0.0 0.0
1.25 0.0 -0.0033524364698678255
0.0 0.0
1.1875 0.0 -0.0033

0.0 0.0
1.3125 0.0 -0.003423108719289303
0.0 0.0
1.21875 -0.0128173828125 -0.0013954564929008484
0.0 0.0
1.5 -0.0098876953125 -0.0026482834946364164
0.0 0.0
1.4375 -0.004150390625 -0.003587582381442189
0.0 0.0
1.46875 -0.0013427734375 -0.004986893851310015
0.0 0.0
1.625 0.0 -0.004453639034181833
0.0 0.0
1.34375 0.0 -0.0034410979133099318
0.0 0.0
1.53125 0.0 -0.0063630761578679085
0.0 0.0
1.5 0.0 -0.0027189557440578938
-0.0859375 -0.1171875
1.375 0.0 -0.007926860824227333
0.0 0.0
1.46875 -0.002197265625 -0.002806332428008318
0.0 0.0
1.53125 0.0 -0.005299136508256197
0.0 0.0
1.53125 0.0 -0.0028975638560950756
0.0 0.0
1.5 -0.0003662109375 -0.004737613257020712
0.0 0.0
1.3125 -0.0045166015625 -0.0022062603384256363
0.0 0.0
1.4375 0.0 -0.0032483553513884544
0.0 0.0
1.53125 -0.0147705078125 -0.003776470199227333
0.0 0.0
1.4375 0.0 -0.003353721462190151
0.0 0.0
1.3125 -0.0201416015625 -0.008853310719132423
0.0 0.0
1.5625 0.0 -0.004977899137884378
0.0 0.0
1.46875 -0.0001220703125 -0.0031417044

0.0 0.0
1.28125 -0.011474609375 -0.0024529709480702877
0.0 0.0
1.59375 0.0 -0.0021946958731859922
0.0 0.0
1.5 0.0 -0.0028692949563264847
0.0 0.0
1.40625 0.0 -0.00675627076998353
0.0 0.0
1.125 0.0 -0.005313271190971136
0.0 0.0
1.4375 -0.0015869140625 -0.005080695264041424
0.0 0.0
1.375 0.0 -0.002724095480516553
0.0 0.0
1.5625 -0.015625 -0.0038779813330620527
0.0 0.0
1.46875 0.0 -0.003453947603702545
0.0 0.0
1.53125 0.0 -0.0031982422806322575
0.0 0.0
1.21875 0.0 -0.0029194080270826817
0.0 0.0
1.4375 0.0 -0.003804739098995924
0.0 0.0
1.34375 0.0 -0.004939350765198469
0.0 0.0
1.5625 0.0 -0.004514032043516636
0.0 0.0
1.28125 -0.0150146484375 -0.004335423931479454
0.0 0.0
1.5625 0.0 -0.002707391045987606
0.0 0.0
1.28125 -0.0076904296875 -0.004427940119057894
0.0 0.0
1.09375 0.0 -0.002812757156789303
0.0 0.0
1.5625 0.0 -0.0032701995223760605
0.0 0.0
1.5625 0.0 -0.0021304483525455
0.0 0.0
1.4375 0.0 -0.005810547154396772
0.0 0.0
1.3125 0.0 -0.005128238350152969
0.0 0.0
1.5 0.0 -0.0031481292098

0.0 0.0
1.46875 0.0 -0.004682360216975212
0.0 0.0
1.53125 0.0 -0.004651521798223257
0.0 0.0
1.21875 0.0 -0.003975637722760439
0.0 0.0
1.6875 -0.0001220703125 -0.0020160877611488104
0.0 0.0
1.46875 0.0 -0.002630294067785144
0.0 0.0
1.3125 0.0 -0.005058851093053818
0.0 0.0
1.53125 0.0 -0.0037083677016198635
0.0 0.0
1.4375 0.0 -0.0026598479598760605
0.0 0.0
1.53125 0.0 -0.006315532606095076
0.0 0.0
1.34375 0.0 -0.0025814659893512726
0.0 0.0
1.40625 -0.0069580078125 -0.003453947603702545
0.0 0.0
1.53125 0.0 -0.004728618543595076
-0.03125 -0.01953125
1.40625 -0.0003662109375 -0.0025814659893512726
0.0 0.0
1.5 -0.0001220703125 -0.005643503740429878
0.0 0.0
1.53125 0.0 -0.0036916634999215603
0.0 0.0
1.25 0.0 -0.002225534524768591
0.0 0.0
1.53125 0.0 -0.0027253804728388786
0.0 0.0
1.21875 -0.000244140625 -0.003804739098995924
0.0 0.0
1.53125 0.0 -0.002551912097260356
0.0 0.0
1.5625 0.0 -0.005229749251157045
0.0 0.0
1.25 0.0 -0.004210783634334803
0.0 0.0
1.40625 0.0 -0.004308439791202545
0.0 0.

0.0 0.0
1.15625 0.0 -0.005499589256942272
0.0 0.0
1.625 0.0 -0.005629369057714939
0.0 0.0
1.4375 0.0 -0.003118575317785144
0.0 0.0
1.28125 -0.0054931640625 -0.0029977899976074696
0.0 0.0
1.53125 0.0 -0.005774568300694227
0.0 0.0
1.34375 0.0 -0.002334755379706621
0.0 0.0
1.59375 0.0 -0.0021882711444050074
0.0 0.0
1.34375 -0.014404296875 -0.0029823705554008484
0.0 0.0
1.21875 -0.0001220703125 -0.004493472632020712
0.0 0.0
1.375 0.0 -0.003421823726966977
0.0 0.0
1.46875 0.0 -0.003966643009334803
0.0 0.0
1.375 0.0 -0.00792172085493803
0.0 0.0
1.65625 0.0 -0.0008609169744886458
0.0 0.0
1.25 -0.0001220703125 -0.0058760796673595905
0.0 0.0
1.59375 -0.0059814453125 -0.003011924447491765
0.0 0.0
1.59375 -0.0050048828125 -0.004215923137962818
0.0 0.0
1.40625 0.0 -0.004251901991665363
0.0 0.0
1.375 0.0 -0.006417043972760439
0.0 0.0
1.28125 0.0 -0.005617804359644651
0.0 0.0
1.4375 -0.0146484375 -0.004986893851310015
0.0 0.0
1.34375 -0.00732421875 -0.002339895348995924
0.0 0.0
1.34375 0.0 -0.005497

In [ ]:
train() #debug

-1.758781909942627 -1.758781909942627
1.5 -1.6732417345046997 -1.789136290550232
-1.6059935092926025 -1.605993628501892
1.09375 -1.562266230583191 -1.7752883434295654
-1.3787505626678467 -1.3787506818771362
1.09375 -1.4027016162872314 -1.7065988779067993
-1.4835193157196045 -1.4835193157196045
1.09375 -1.106798768043518 -1.4930269718170166
-1.4113831520080566 -1.4113831520080566
1.125 -0.9243863821029663 -1.3320039510726929
-0.6587601900100708 -0.6587600708007812
1.09375 -0.8840252161026001 -1.2160131931304932
-1.0985782146453857 -1.0985779762268066
1.125 -0.7760924696922302 -1.0423139333724976
-0.7114690542221069 -0.7114690542221069
0.96875 -0.7488306164741516 -1.0413395166397095
-0.22774064540863037 -0.22774076461791992
1.25 -0.7758721113204956 -1.089994192123413
-0.30479907989501953 -0.3047991991043091
1.125 -0.6795670390129089 -0.9874025583267212
-0.5933346748352051 -0.5933349132537842
1.125 -0.602640688419342 -0.9364912509918213
-1.1089246273040771 -1.1089247465133667
1.09375 -0.7

0.96875 -0.07037464529275894 -0.13547846674919128
-4.291534423828125e-06 -4.291534423828125e-06
0.875 -0.07338665425777435 -0.19730189442634583
-4.76837158203125e-06 -4.76837158203125e-06
0.9375 -0.12770742177963257 -0.21985769271850586
-0.04896259307861328 -0.04896259307861328
1.03125 -0.14212727546691895 -0.1943724900484085
-0.06953859329223633 -0.06953859329223633
1.1875 -0.1342906355857849 -0.21100834012031555
-0.139349102973938 -0.139349102973938
1.3125 -0.10475131869316101 -0.22587646543979645
-0.09925079345703125 -0.09924983978271484
1.0 -0.11285124719142914 -0.2419104427099228
-0.18470287322998047 -0.18470287322998047
1.21875 -0.13094735145568848 -0.22318150103092194
-0.000835418701171875 -0.000835418701171875
1.09375 -0.12086402624845505 -0.22730587422847748
-0.002658843994140625 -0.002658843994140625
0.90625 -0.11305081099271774 -0.262172132730484
-0.19748878479003906 -0.19748878479003906
1.03125 -0.0989437997341156 -0.25045880675315857
-0.000812530517578125 -0.00081253051757

1.125 -0.08877389132976532 -0.22041675448417664
-0.857365608215332 -0.857365608215332
1.03125 -0.10282008349895477 -0.23796118795871735
0.0 0.0
1.0625 -0.10307158529758453 -0.2038205862045288
-0.007709503173828125 -0.007709503173828125
0.84375 -0.0952889621257782 -0.180478036403656
-0.0324249267578125 -0.0324249267578125
1.15625 -0.06842869520187378 -0.19764846563339233
0.0 0.0
0.75 -0.06478255987167358 -0.14065362513065338
-0.08437442779541016 -0.08437347412109375
0.90625 -0.10885405540466309 -0.15705960988998413
-0.010466575622558594 -0.010466575622558594
0.90625 -0.0929768979549408 -0.15284384787082672
-0.008722305297851562 -0.008722305297851562
0.84375 -0.09801364690065384 -0.19389091432094574
-0.011749267578125 -0.011749267578125
0.84375 -0.059621214866638184 -0.12892359495162964
0.0 0.0
0.78125 -0.03368188813328743 -0.09492948651313782
-0.06807804107666016 -0.06807804107666016
0.875 -0.06414791196584702 -0.16287630796432495
0.0 0.0
0.96875 -0.07544748485088348 -0.1260664910078048

-0.2380509376525879 -0.2380509376525879
0.78125 -0.014150306582450867 -0.06417032331228256
0.0 0.0
0.8125 -0.03303894028067589 -0.09490744024515152
-0.00084686279296875 -0.00084686279296875
0.9375 -0.015321612358093262 -0.06281837075948715
-0.00255584716796875 -0.00255584716796875
0.8125 -0.04600658267736435 -0.07525818049907684
0.0 0.0
0.90625 -0.0048134177923202515 -0.05099944397807121
0.0 0.0
1.0625 -0.031366005539894104 -0.06931223720312119
0.0 0.0
1.0 -0.03744363784790039 -0.09426837414503098
-1.9073486328125e-05 -1.9073486328125e-05
1.0 -0.04049861058592796 -0.09334025532007217
0.0 0.0
1.0 -0.08075422048568726 -0.09220099449157715
0.0 0.0
0.875 -0.020290324464440346 -0.06029333546757698
-0.9056978225708008 -0.9056978225708008
0.9375 -0.004223156720399857 -0.050168026238679886
0.0 0.0
1.0 -0.03325704485177994 -0.06726181507110596
-9.5367431640625e-06 -9.5367431640625e-06
0.78125 -0.027760686352849007 -0.05574537813663483
-0.0001537799835205078 -0.0001537799835205078
0.84375 -0.018

0.0 0.0
0.9375 -0.024399325251579285 -0.03218046575784683
0.0 0.0
0.875 -0.0011382102966308594 -0.04784088209271431
0.0 0.0
0.8125 -0.029751703143119812 -0.0689554512500763
0.0 0.0
0.78125 -0.001463320106267929 -0.045728471130132675
-2.0797042846679688 -2.0797042846679688
0.875 -0.043425071984529495 -0.05934692919254303
0.0 0.0
0.78125 -0.001393437385559082 -0.03239941596984863
-0.43795013427734375 -0.43795013427734375
0.90625 -0.03262723609805107 -0.08527219295501709
-0.001377105712890625 -0.001377105712890625
0.75 -0.06876704096794128 -0.1256496161222458
-0.0009476244449615479 -0.0009476244449615479
0.96875 -0.04456038400530815 -0.08222275972366333
0.0 0.0
0.9375 -0.09454785287380219 -0.12815313041210175
-0.2696037292480469 -0.2696037292480469
0.90625 -0.09661276638507843 -0.1703392118215561
0.0 0.0
1.0 -0.10723605751991272 -0.15465453267097473
0.0 0.0
0.875 -0.04278644919395447 -0.12717781960964203
-0.8718843460083008 -0.8718833923339844
0.6875 -0.08153635263442993 -0.12425621598958

...

-0.00017547607421875 -0.00017547607421875
0.875 -0.01791033148765564 -0.04684406891465187
-1.52587890625e-05 -1.52587890625e-05
1.3125 -0.03242560103535652 -0.04122621938586235
-3.814697265625e-06 -3.814697265625e-06
0.90625 -0.0030275173485279083 -0.044813744723796844
0.0 0.0
0.84375 -0.014104928821325302 -0.05080924928188324
0.0 0.0
0.875 -0.0030808299779891968 -0.035302791744470596
-0.03975868225097656 -0.03975868225097656
0.9375 -0.010612420737743378 -0.05139885097742081
-0.001461029052734375 -0.001461029052734375
0.90625 -0.03180307149887085 -0.04276268929243088
0.0 0.0
0.96875 -0.02842700481414795 -0.06042585149407387
0.0 0.0
0.75 -0.004460856318473816 -0.03451552242040634
-0.000705718994140625 -0.000705718994140625
1.09375 -0.02279742807149887 -0.02677195519208908
0.0 0.0
0.90625 -0.02370816469192505 -0.03736451640725136
0.0 0.0
1.0 -0.000986337661743164 -0.022713450714945793
0.0 0.0
0.90625 -0.002954438328742981 -0.036499567329883575
0.0 0.0
0.875 -0.025266006588935852 -0.03299

0.0 0.0
0.875 -0.021300330758094788 -0.030860362574458122
0.0 0.0
0.84375 -0.032621026039123535 -0.04222756624221802
0.0 0.0
0.9375 -0.00501839816570282 -0.035102177411317825
0.0 0.0
0.90625 -0.016609076410531998 -0.02849009446799755
0.0 0.0
0.90625 -0.0237625390291214 -0.028618479147553444
0.0 0.0
1.0625 -0.016625046730041504 -0.040652114897966385
0.0 0.0
1.125 -0.018362388014793396 -0.03656819090247154
0.0 0.0
0.75 -0.0021596550941467285 -0.030733540654182434
0.0 0.0
0.84375 -0.021046221256256104 -0.035337723791599274
-0.07004547119140625 -0.07004547119140625
1.0 -0.006887013092637062 -0.035559482872486115
0.0 0.0
0.9375 -0.03695555031299591 -0.04633766785264015
-0.030714988708496094 -0.030714988708496094
1.125 -0.013861577957868576 -0.03653427213430405
0.0 0.0
0.84375 -0.030157947912812233 -0.03332515060901642
-7.62939453125e-06 -7.62939453125e-06
0.96875 -0.00477173924446106 -0.03975602984428406
0.0 0.0
0.8125 -0.013594388961791992 -0.0349065326154232
0.0 0.0
1.125 -0.0017970502376

1.0 -0.0018825232982635498 -0.03968684375286102
0.0 0.0
0.9375 -0.035721469670534134 -0.034470051527023315
-2.86102294921875e-06 -2.86102294921875e-06
0.84375 -0.02317126840353012 -0.046853676438331604
-0.49500560760498047 -0.49500560760498047
0.84375 -0.013944663107395172 -0.03484618663787842
0.0 0.0
1.03125 -0.017319485545158386 -0.04669458791613579
0.0 0.0
0.8125 -0.026171892881393433 -0.033868301659822464
0.0 0.0
1.03125 -0.005611035972833633 -0.03205748647451401
0.0 0.0
1.0 -0.009900972247123718 -0.03734416514635086
0.0 0.0
0.875 -0.0035956716164946556 -0.026614975184202194
-0.0005817413330078125 -0.0005817413330078125
0.84375 -0.0016430318355560303 -0.024656783789396286
-0.00066375732421875 -0.00066375732421875
1.09375 -0.005115047097206116 -0.031206702813506126
-0.000518798828125 -0.000518798828125
1.0 -0.006088584661483765 -0.03079487942159176
0.0 0.0
0.84375 -0.029269419610500336 -0.023126307874917984
0.0 0.0
1.0 -0.04285799339413643 -0.024166865274310112
0.0 0.0
0.65625 -0.01

0.96875 -0.020149052143096924 -0.03082277998328209
-0.15301513671875 -0.15301513671875
0.9375 -0.024340033531188965 -0.039465874433517456
-0.00017547607421875 -0.00017547607421875
0.71875 -0.007740139961242676 -0.024496737867593765
-0.0424041748046875 -0.0424041748046875
1.0 -0.010495156049728394 -0.040660977363586426
0.0 0.0
1.03125 -0.018564224243164062 -0.042275961488485336
0.0 0.0
0.96875 -0.0234832763671875 -0.032564710825681686
0.0 0.0
0.9375 -0.004945874214172363 -0.03175295889377594
-0.22104644775390625 -0.22104644775390625
0.8125 -0.03123977780342102 -0.035762250423431396
0.0 0.0
0.8125 -0.0061836838722229 -0.02293330430984497
0.0 0.0
0.9375 -0.01601874828338623 -0.03052259050309658
0.0 0.0
0.84375 -0.009030163288116455 -0.03729189559817314
-0.000621795654296875 -0.000621795654296875
0.9375 -0.014922261238098145 -0.032515786588191986
0.0 0.0
0.59375 -0.0011221766471862793 -0.03401613235473633
0.0 0.0
0.8125 -0.04001474380493164 -0.031111327931284904
0.0 0.0
0.875 -0.0334104299

0.75 -0.04004859924316406 -0.03174212947487831
0.0 0.0
0.75 -0.02104783058166504 -0.027540966868400574
0.0 0.0
0.875 -0.002538338303565979 -0.025586435571312904
0.0 0.0
0.96875 -0.020076438784599304 -0.03487405553460121
0.0 0.0
0.96875 -0.002553015947341919 -0.03072000853717327
0.0 0.0
1.09375 -0.02925475686788559 -0.04539842903614044
-0.00025177001953125 -0.00025177001953125
1.09375 -0.012181758880615234 -0.05102163925766945
-0.00363922119140625 -0.00363922119140625
1.03125 -0.004627212882041931 -0.030480671674013138
-0.01493072509765625 -0.01493072509765625
0.9375 -0.014723993837833405 -0.02905363403260708
-0.00215911865234375 -0.00215911865234375
0.84375 -0.010477341711521149 -0.041610512882471085
0.0 0.0
1.0 -0.014729440212249756 -0.032954394817352295
-0.316436767578125 -0.31642913818359375
0.96875 -0.005622446537017822 -0.05524148792028427
0.0 0.0
0.90625 -0.002480924129486084 -0.02245543710887432
0.0 0.0
0.90625 -0.03041417896747589 -0.024702163413167
0.0 0.0
0.8125 -0.0110563188

In [ ]:
train() #supervised leraning #ignore bug for now, just use no decoder layers for now

-1.784734845161438 -1.7847347259521484
1.1875 -1.6385347843170166 -1.779285192489624
-1.6953375339508057 -1.6953375339508057
1.03125 -1.276209831237793 -1.6315699815750122
-0.9468300342559814 -0.9468298554420471
0.9375 -0.997090220451355 -1.4294099807739258
-0.81275475025177 -0.8127548694610596
1.09375 -0.6309516429901123 -0.96797114610672
-0.4753851890563965 -0.4753851890563965
0.96875 -0.7877801656723022 -1.038719892501831
-1.994410514831543 -1.994410753250122
1.0625 -0.7343428134918213 -0.9721660614013672
-0.28999829292297363 -0.28999853134155273
0.96875 -0.7491337060928345 -1.0500417947769165
-0.7258038520812988 -0.7258038520812988
0.875 -0.7398081421852112 -1.0601119995117188
-0.5195682048797607 -0.5195679664611816
1.03125 -0.8222090005874634 -1.1063042879104614
-0.6793642044067383 -0.6793640851974487
0.96875 -0.6826370358467102 -0.9509661793708801
-0.32068395614624023 -0.32068395614624023
0.84375 -0.48364943265914917 -0.7483641505241394
-0.9422502517700195 -0.9422500133514404
1.2

-0.5858006477355957 -0.5858006477355957
0.9375 -0.5082038044929504 -0.8170114755630493
-1.2826223373413086 -1.2826223373413086
0.84375 -0.3725971281528473 -0.6275510191917419
-0.8178272247314453 -0.8178272247314453
0.96875 -0.47595149278640747 -0.7074574828147888
-0.08332061767578125 -0.08332061767578125
0.90625 -0.38304832577705383 -0.6393765211105347
-1.7603001594543457 -1.7602996826171875
0.8125 -0.3392532169818878 -0.555993378162384
-0.3614330291748047 -0.3614320755004883
1.0 -0.4527445435523987 -0.6408703327178955
-0.03311634063720703 -0.03311634063720703
1.0 -0.42184197902679443 -0.6383225917816162
-0.8391323089599609 -0.8391318321228027
1.0625 -0.5231079459190369 -0.6820418238639832
-0.9122319221496582 -0.9122309684753418
0.875 -0.37267428636550903 -0.6124036312103271
-0.6704316139221191 -0.6704311370849609
0.96875 -0.3447869122028351 -0.5854079127311707
-0.7145581245422363 -0.7145576477050781
1.0 -0.48058897256851196 -0.6627992391586304
-0.762453556060791 -0.7624540328979492
0.

-0.23169803619384766 -0.23169803619384766
0.90625 -0.25729677081108093 -0.46187183260917664
-0.07538747787475586 -0.07538747787475586
1.03125 -0.36568769812583923 -0.5912472009658813
-0.6056017875671387 -0.6056017875671387
0.9375 -0.2974926233291626 -0.5319164991378784
-1.1163451671600342 -1.116344928741455
0.875 -0.34489965438842773 -0.5365282893180847
-0.1596050262451172 -0.1596050262451172
1.09375 -0.4001757502555847 -0.5842122435569763
-0.02315998077392578 -0.02315998077392578
0.90625 -0.3289686441421509 -0.511396050453186
-0.7583291530609131 -0.7583292722702026
0.8125 -0.36334848403930664 -0.6201894283294678
-0.8298366069793701 -0.8298375606536865
0.78125 -0.4419322907924652 -0.6158143877983093
-0.5146164894104004 -0.5146164894104004
1.03125 -0.4297419786453247 -0.6178345084190369
-0.6385459899902344 -0.6385459899902344
1.0625 -0.49025100469589233 -0.6752358078956604
-0.14831972122192383 -0.14831972122192383
0.90625 -0.4639662802219391 -0.65925532579422
-0.5350723266601562 -0.5350

-1.5985698699951172 -1.5985703468322754
1.09375 -0.4162043631076813 -0.5877440571784973
-1.0313260555267334 -1.0313265323638916
0.90625 -0.35118332505226135 -0.5946739315986633
-0.08951377868652344 -0.08951377868652344
0.90625 -0.38097548484802246 -0.6452524662017822
-0.5641279220581055 -0.5641288757324219
0.875 -0.35436123609542847 -0.5864516496658325
-0.656092643737793 -0.656092643737793
0.90625 -0.4219806492328644 -0.6892750859260559
-0.7708244323730469 -0.7708244323730469
0.8125 -0.41517361998558044 -0.6097408533096313
-0.8530664443969727 -0.8530664443969727
0.96875 -0.36098402738571167 -0.6580576300621033
-0.2077469825744629 -0.2077469825744629
1.0625 -0.39815443754196167 -0.6668745279312134
-0.5615077018737793 -0.5615077018737793
0.78125 -0.3228151500225067 -0.6244373917579651
-0.2477397918701172 -0.2477402687072754
0.9375 -0.40587514638900757 -0.6516308784484863
-0.3218827247619629 -0.3218832015991211
0.875 -0.36630359292030334 -0.667252779006958
-0.7124171257019043 -0.712417602

-0.054225921630859375 -0.054225921630859375
0.96875 -0.29215696454048157 -0.5845606327056885
-0.168212890625 -0.168212890625
0.9375 -0.3938565254211426 -0.6518381237983704
-0.7542624473571777 -0.7542619705200195
0.84375 -0.35973089933395386 -0.6934251189231873
-2.1775410175323486 -2.1775410175323486
0.96875 -0.31960606575012207 -0.5813081860542297
-0.09840536117553711 -0.09840536117553711
0.90625 -0.3487224578857422 -0.565805971622467
-0.5022282600402832 -0.5022282600402832
0.875 -0.34752142429351807 -0.627158522605896
-1.3471975326538086 -1.3471970558166504
0.84375 -0.27962589263916016 -0.5511021614074707
-0.25285816192626953 -0.25285816192626953
0.84375 -0.3646857738494873 -0.597869873046875
-0.5768237113952637 -0.5768241882324219
0.9375 -0.26085349917411804 -0.48675477504730225
-0.7944512367248535 -0.7944512367248535
0.78125 -0.400831937789917 -0.5741671323776245
-0.18862676620483398 -0.18862628936767578
0.9375 -0.383411705493927 -0.6524857878684998
-0.029621601104736328 -0.02962207

...

0.59375 -0.35907167196273804 -0.57542484998703
-0.341778039932251 -0.341778039932251
0.78125 -0.3425731956958771 -0.5686413645744324
-0.06440150737762451 -0.06440150737762451
0.59375 -0.2773315906524658 -0.5212938189506531
-1.025723934173584 -1.0257240533828735
0.71875 -0.30987197160720825 -0.5639452934265137
-0.32237887382507324 -0.32237911224365234
0.71875 -0.3329387605190277 -0.5996226668357849
-4.953517436981201 -4.953516483306885
0.71875 -0.4004899561405182 -0.6489564776420593
-1.342909336090088 -1.342909812927246
0.78125 -0.27270805835723877 -0.5987826585769653
-0.3703916072845459 -0.3703913688659668
0.8125 -0.4288334846496582 -0.6797225475311279
-0.8572711944580078 -0.8572711944580078
0.78125 -0.3528567850589752 -0.6063424348831177
-0.3115427494049072 -0.3115425109863281
0.625 -0.25671815872192383 -0.5292764902114868
-0.0954887866973877 -0.0954887866973877
0.5 -0.3467022776603699 -0.6197230815887451
-0.04154014587402344 -0.04154014587402344
0.625 -0.3254314064979553 -0.594232499

-1.1446847915649414 -1.1446847915649414
0.6875 -0.2806398272514343 -0.5775889754295349
-0.08584904670715332 -0.08584904670715332
0.75 -0.30314505100250244 -0.5800662040710449
-1.169330358505249 -1.1693305969238281
0.5625 -0.2983766496181488 -0.5925386548042297
-0.8954329490661621 -0.895432710647583
0.90625 -0.36967918276786804 -0.6006017923355103
-0.33292078971862793 -0.33292078971862793
0.71875 -0.3946722447872162 -0.6676899194717407
-0.043662309646606445 -0.043662071228027344
0.65625 -0.34868571162223816 -0.639680802822113
-0.08163690567016602 -0.08163714408874512
0.53125 -0.2549470365047455 -0.5275441408157349
-0.5649087429046631 -0.5649087429046631
0.5625 -0.3259732723236084 -0.5444114804267883
-0.14678478240966797 -0.14678454399108887
0.65625 -0.31923216581344604 -0.5605392456054688
-0.06808710098266602 -0.06808710098266602
0.625 -0.32208067178726196 -0.5685445070266724
-0.573167085647583 -0.5731672048568726
0.71875 -0.3913508653640747 -0.6623485088348389
-0.3854501247406006 -0.38

0.625 -0.38581395149230957 -0.6376855373382568
-0.6777099370956421 -0.6777098178863525
0.59375 -0.30004629492759705 -0.5885159969329834
-0.05675482749938965 -0.05675482749938965
0.53125 -0.2534054219722748 -0.5166978240013123
-0.1791844367980957 -0.1791844367980957
0.625 -0.33018872141838074 -0.6123661398887634
-0.18653512001037598 -0.18653512001037598
0.8125 -0.31491994857788086 -0.5950020551681519
-0.28542232513427734 -0.28542232513427734
0.6875 -0.29064857959747314 -0.5624212622642517
-1.2976272106170654 -1.2976276874542236
0.65625 -0.26926642656326294 -0.6038798689842224
-0.24248898029327393 -0.24248921871185303
0.65625 -0.343260258436203 -0.623701810836792
-0.9781310558319092 -0.9781312942504883
0.625 -0.3708896338939667 -0.5814313888549805
-1.2593731880187988 -1.2593731880187988
0.65625 -0.3140546679496765 -0.6015939116477966
-0.5450232028961182 -0.5450234413146973
0.6875 -0.313049852848053 -0.5971845984458923
-0.8156850337982178 -0.8156847953796387
0.65625 -0.37784814834594727 -

-0.286344051361084 -0.28634417057037354
0.59375 -0.31166499853134155 -0.5959645509719849
-0.9803409576416016 -0.9803409576416016
0.6875 -0.40168678760528564 -0.621867835521698
-0.9887349605560303 -0.9887349605560303
0.6875 -0.3447107970714569 -0.5651029348373413
-2.136915922164917 -2.136915922164917
0.75 -0.4003198444843292 -0.599553644657135
-0.34078192710876465 -0.34078192710876465
0.6875 -0.36193209886550903 -0.5701152086257935
-0.8136773109436035 -0.8136773109436035
0.6875 -0.31994539499282837 -0.5609307289123535
-0.3013010025024414 -0.3013012409210205
0.40625 -0.3255409598350525 -0.5756430625915527
-0.027475833892822266 -0.027475833892822266
0.5 -0.3362921476364136 -0.533726692199707
-0.15168190002441406 -0.15168190002441406
0.75 -0.3666580319404602 -0.6956295371055603
-0.09924602508544922 -0.09924602508544922
0.75 -0.3223685324192047 -0.6148650646209717
-0.2923574447631836 -0.2923574447631836
0.5625 -0.34604156017303467 -0.545041024684906
-0.01841127872467041 -0.01841127872467041

0.53125 -0.2750433683395386 -0.5393218398094177
-0.024244189262390137 -0.024244189262390137
0.59375 -0.37603646516799927 -0.5948454737663269
-0.02436518669128418 -0.02436518669128418
0.625 -0.37392061948776245 -0.6626488566398621
-0.10291194915771484 -0.10291194915771484
0.625 -0.31645986437797546 -0.5651468634605408
-0.3469045162200928 -0.3469045162200928
0.71875 -0.3244400918483734 -0.6402063965797424
-0.029179096221923828 -0.029179096221923828
0.65625 -0.40988248586654663 -0.5864284634590149
-0.07206153869628906 -0.07206153869628906
0.6875 -0.2964901924133301 -0.5925266146659851
-0.4896838665008545 -0.4896838665008545
0.71875 -0.3080761432647705 -0.5557929277420044
-0.11474990844726562 -0.11474990844726562
0.71875 -0.2982109785079956 -0.601865828037262
-0.58648681640625 -0.5864870548248291
0.59375 -0.3368750214576721 -0.6052367091178894
-1.3931858539581299 -1.393186092376709
0.625 -0.32800301909446716 -0.580929160118103
-0.41658449172973633 -0.4165842533111572
0.625 -0.3408980369567

In [ ]:
train() #greedy basline binary positive reinforcement #ignore bug for now, just use no decoder layers for now

-1.8119299411773682 -1.8119299411773682
1.5 -1.6764190196990967 -1.7871328592300415
-2.255446672439575 -2.255446672439575
1.25 -1.4668207168579102 -1.7510359287261963
-2.370650053024292 -2.370649814605713
1.21875 -1.0405840873718262 -1.552836537361145
-0.8055745363235474 -0.8055741786956787
1.09375 -0.7276149988174438 -1.1789321899414062
-0.810910701751709 -0.8109108209609985
1.34375 -0.651413083076477 -1.0360790491104126
-0.7873889207839966 -0.7873889207839966
1.0 -0.6046614646911621 -0.9864051938056946
-2.0000405311584473 -2.000040292739868
1.34375 -0.4587671160697937 -0.7629411816596985
-2.359726905822754 -2.359727382659912
1.125 -0.41122663021087646 -0.7524784803390503
-0.11074745655059814 -0.11074745655059814
1.03125 -0.4264129102230072 -0.6638580560684204
-0.04827284812927246 -0.04827284812927246
1.0625 -0.3154336214065552 -0.6110091805458069
-0.19870567321777344 -0.19870591163635254
1.0 -0.34231168031692505 -0.6547992825508118
-0.4039567708969116 -0.40395665168762207
1.09375 -0.

0.9375 -0.4048321843147278 -0.7011016607284546
-0.7651287913322449 -0.7651287913322449
0.90625 -0.3318459987640381 -0.6283529996871948
-0.005755901336669922 -0.005755901336669922
1.0625 -0.32127678394317627 -0.5522121787071228
-0.40451979637145996 -0.4045198857784271
1.03125 -0.2914699912071228 -0.613564133644104
-0.04326295852661133 -0.04326295852661133
1.0625 -0.322573721408844 -0.6704458594322205
-0.604630172252655 -0.604630172252655
1.1875 -0.3449590802192688 -0.5871202349662781
-0.10781621932983398 -0.10781621932983398
0.90625 -0.36533376574516296 -0.639354944229126
-0.534775972366333 -0.5347759127616882
1.0 -0.3933728337287903 -0.6970723271369934
-0.02474498748779297 -0.02474498748779297
1.03125 -0.4207753539085388 -0.7350602149963379
-0.2336522340774536 -0.2336522340774536
0.8125 -0.3885616660118103 -0.726802408695221
-0.4790440797805786 -0.4790440797805786
0.96875 -0.38709816336631775 -0.7192818522453308
-1.1826658248901367 -1.1826657056808472
0.84375 -0.37001389265060425 -0.61

-0.30672669410705566 -0.30672669410705566
1.0625 -0.26204943656921387 -0.5159765481948853
-0.015753507614135742 -0.015753507614135742
0.90625 -0.25430727005004883 -0.5119104981422424
-0.2381986379623413 -0.23819869756698608
1.0625 -0.2622147798538208 -0.5542340278625488
-1.1101717948913574 -1.1101720333099365
0.96875 -0.2979940176010132 -0.5408753752708435
-0.4644591808319092 -0.4644591808319092
0.78125 -0.3330947756767273 -0.5994685292243958
-1.1161410808563232 -1.116140604019165
0.75 -0.3060281276702881 -0.5631024241447449
-0.8139331340789795 -0.8139331340789795
0.90625 -0.4113045334815979 -0.6874067187309265
-0.02748870849609375 -0.02748870849609375
0.84375 -0.29819950461387634 -0.5539159178733826
-0.8159685134887695 -0.81596839427948
0.96875 -0.35566502809524536 -0.6212480664253235
-2.1235525608062744 -2.1235527992248535
0.96875 -0.3207012414932251 -0.6393078565597534
-0.15706396102905273 -0.15706348419189453
1.0 -0.2749423384666443 -0.5139970779418945
-0.13435983657836914 -0.13435

0.75 -0.3261301517486572 -0.6269680261611938
-0.0960075855255127 -0.09600746631622314
1.09375 -0.2773497402667999 -0.5694929957389832
-0.9715629816055298 -0.971562922000885
0.96875 -0.29401642084121704 -0.5898861885070801
-0.24475514888763428 -0.24475565552711487
1.0625 -0.36963602900505066 -0.6593155860900879
-1.3671010732650757 -1.3671001195907593
0.78125 -0.23012496531009674 -0.47743383049964905
-4.177735805511475 -4.177736282348633
0.8125 -0.2054775357246399 -0.46446534991264343
-0.025766849517822266 -0.025766849517822266
0.90625 -0.26963698863983154 -0.5504636168479919
-0.01109004020690918 -0.01109004020690918
0.96875 -0.2791028320789337 -0.5066097378730774
-0.9986138343811035 -0.9986138343811035
0.90625 -0.2803063988685608 -0.5654700994491577
-1.1727385520935059 -1.1727375984191895
0.96875 -0.34745973348617554 -0.6208341717720032
-0.6919469833374023 -0.6919465065002441
0.9375 -0.34614938497543335 -0.6954677700996399
-0.9213771820068359 -0.921377420425415
0.84375 -0.35280123353004

0.9375 -0.36897578835487366 -0.659103512763977
-0.45293402671813965 -0.45293402671813965
0.96875 -0.361196368932724 -0.6661390662193298
-0.08559036254882812 -0.08559036254882812
1.03125 -0.33177515864372253 -0.6597674489021301
-0.3273879289627075 -0.3273874521255493
1.09375 -0.43358534574508667 -0.7699681520462036
-1.7147603034973145 -1.714759349822998
1.0 -0.2972222566604614 -0.6199411153793335
-2.697406768798828 -2.6974072456359863
0.78125 -0.3933977484703064 -0.6534074544906616
-0.13830924034118652 -0.13830924034118652
0.84375 -0.291006475687027 -0.5691721439361572
-0.20278358459472656 -0.20278358459472656
0.78125 -0.26302123069763184 -0.5362626314163208
-0.05655360221862793 -0.05655360221862793
0.96875 -0.27843135595321655 -0.5483442544937134
-3.597808361053467 -3.597808361053467
1.03125 -0.2522624433040619 -0.5054936408996582
-4.1243977546691895 -4.124398231506348
1.03125 -0.31587493419647217 -0.6031764149665833
-0.3122878074645996 -0.3122878074645996
0.96875 -0.26279136538505554 

...

-3.2984631061553955 -3.2984633445739746
0.625 -0.36165082454681396 -0.6531339287757874
-4.598930835723877 -4.598930358886719
0.71875 -0.33083683252334595 -0.6205573081970215
-0.08393692970275879 -0.08393716812133789
0.875 -0.4290221631526947 -0.6246206164360046
-0.09196329116821289 -0.09196329116821289
0.8125 -0.4306861162185669 -0.6899293661117554
-0.1348400115966797 -0.1348400115966797
0.53125 -0.30752745270729065 -0.5693647265434265
-0.3244757652282715 -0.32447588443756104
0.78125 -0.3512875437736511 -0.5923520922660828
-0.3076746463775635 -0.3076748847961426
0.71875 -0.35469019412994385 -0.5953767895698547
-0.955528736114502 -0.955528736114502
0.78125 -0.3788129389286041 -0.6376653909683228
-0.5859889984130859 -0.5859889984130859
0.65625 -0.32856500148773193 -0.5646271109580994
-0.20995616912841797 -0.20995616912841797
0.71875 -0.3288291096687317 -0.6162102222442627
-0.18803930282592773 -0.18803930282592773
0.71875 -0.3691563606262207 -0.6283475160598755
-0.12991638481616974 -0.129

-0.6799435019493103 -0.6799435019493103
0.90625 -0.30813920497894287 -0.5789121985435486
-0.08505868911743164 -0.08505868911743164
0.75 -0.312348335981369 -0.6019607782363892
-0.10992145538330078 -0.10992145538330078
0.96875 -0.4256671965122223 -0.6532602906227112
-2.177245616912842 -2.177245855331421
0.6875 -0.42160046100616455 -0.5831013917922974
-0.49507880210876465 -0.49507927894592285
0.5625 -0.3513341248035431 -0.607877790927887
-0.34296369552612305 -0.34296393394470215
0.71875 -0.32921695709228516 -0.5984007716178894
-1.0991833209991455 -1.0991833209991455
0.75 -0.37763017416000366 -0.6353650093078613
-0.14744925498962402 -0.14744925498962402
0.65625 -0.3026381731033325 -0.6030929684638977
-0.3724820613861084 -0.3724820613861084
0.59375 -0.2620435655117035 -0.6279302835464478
-0.6703674793243408 -0.6703677177429199
0.59375 -0.37401866912841797 -0.619912326335907
-0.7584242820739746 -0.7584245204925537
0.78125 -0.39062416553497314 -0.6894452571868896
-2.0580971240997314 -2.058096

-0.08532238006591797 -0.08532238006591797
0.59375 -0.2897639572620392 -0.5639562606811523
-0.10822272300720215 -0.10822272300720215
0.8125 -0.3460248112678528 -0.6230868101119995
-2.9549312591552734 -2.9549314975738525
0.78125 -0.3154505491256714 -0.6301835775375366
-0.05477762222290039 -0.05477762222290039
0.625 -0.3578147292137146 -0.5746048092842102
-1.163272738456726 -1.1632728576660156
0.6875 -0.31758180260658264 -0.5579891204833984
-1.5138576030731201 -1.5138574838638306
0.71875 -0.3568137288093567 -0.5961042046546936
-1.0321955680847168 -1.032195806503296
0.625 -0.3253937363624573 -0.598376452922821
-0.39280247688293457 -0.39280247688293457
0.78125 -0.3312417268753052 -0.582630455493927
-1.7650983333587646 -1.7650983333587646
0.65625 -0.3396068811416626 -0.5828477740287781
-0.27275753021240234 -0.27275753021240234
0.875 -0.31760039925575256 -0.6256552934646606
-0.2891066074371338 -0.2891066074371338
0.5625 -0.36222338676452637 -0.5927018523216248
-0.15812277793884277 -0.15812301

0.875 -0.3690865635871887 -0.6228357553482056
-0.08136272430419922 -0.08136272430419922
0.71875 -0.40913212299346924 -0.6451199650764465
-0.6887531280517578 -0.6887531280517578
0.78125 -0.4113331437110901 -0.6624119281768799
-0.425209641456604 -0.42520955204963684
0.75 -0.3344552516937256 -0.6283993124961853
-0.09275341033935547 -0.09275341033935547
0.71875 -0.4138287305831909 -0.6350969672203064
-0.9691444635391235 -0.9691442251205444
0.8125 -0.44424527883529663 -0.6315013766288757
-2.2835676670074463 -2.283567428588867
0.71875 -0.2998920679092407 -0.5816673040390015
-0.724388599395752 -0.724388599395752
0.65625 -0.33785200119018555 -0.597205400466919
-0.8765637874603271 -0.8765640258789062
0.9375 -0.39307576417922974 -0.6400379538536072
-0.4062833786010742 -0.4062833786010742
0.71875 -0.3221006393432617 -0.6092250943183899
-0.5814943313598633 -0.5814943313598633
0.84375 -0.3978959321975708 -0.6467564702033997
-0.539463996887207 -0.5394644737243652
0.71875 -0.37807169556617737 -0.6514

-0.7894337177276611 -0.7894341945648193
0.625 -0.32111698389053345 -0.6109805703163147
-0.1113886833190918 -0.1113886833190918
0.8125 -0.4242134690284729 -0.6629428863525391
-0.3733031749725342 -0.3733034133911133
0.78125 -0.31376463174819946 -0.6224713921546936
-0.2973780632019043 -0.2973778247833252
0.65625 -0.33673858642578125 -0.6127656102180481
-0.04695582389831543 -0.04695582389831543
0.75 -0.42866596579551697 -0.6805028915405273
-0.04464912414550781 -0.04464912414550781
0.59375 -0.32864105701446533 -0.5810099840164185
-3.464022159576416 -3.464022159576416
0.53125 -0.31043264269828796 -0.6019808053970337
-0.2869429588317871 -0.2869429588317871
0.75 -0.3445962369441986 -0.6228859424591064
-0.27036523818969727 -0.27036499977111816
0.875 -0.2902637720108032 -0.6136983036994934
-0.20435500144958496 -0.20435476303100586
0.6875 -0.3112926185131073 -0.5648438334465027
-3.307938575744629 -3.307938575744629
0.8125 -0.35183459520339966 -0.589920163154602
-0.26414036750793457 -0.26414036750

In [ ]:
train() #greedy binary clipped reinforcement #no decoder layers

-1.8060173988342285 -1.8060176372528076
1.34375 -1.6197352409362793 -1.7801991701126099
-1.7252562046051025 -1.7252562046051025
1.34375 -1.567305564880371 -1.7691564559936523
-1.4363658428192139 -1.4363658428192139
1.375 -1.2112659215927124 -1.6471577882766724
-1.1670968532562256 -1.167096734046936
1.40625 -0.9194777011871338 -1.355891227722168
-0.5469591617584229 -0.5469589233398438
1.28125 -0.6830230951309204 -1.1244502067565918
-4.042876720428467 -4.042877197265625
0.90625 -0.5823938846588135 -0.9820936918258667
-0.3357217311859131 -0.3357217311859131
1.25 -0.43098965287208557 -0.7786258459091187
-0.7164466381072998 -0.7164463996887207
1.125 -0.5923082828521729 -0.8781903982162476
-0.49245619773864746 -0.49245619773864746
1.125 -0.5199861526489258 -0.7795315980911255
-2.0551578998565674 -2.0551581382751465
1.0625 -0.4879685640335083 -0.7540208101272583
-0.6805658340454102 -0.6805658340454102
1.09375 -0.48976999521255493 -0.793505072593689
-0.7259060144424438 -0.7259060144424438
0.93

-0.3823210597038269 -0.38232070207595825
1.0625 -0.39854514598846436 -0.6250473856925964
-0.5290684700012207 -0.5290684103965759
1.21875 -0.35898563265800476 -0.557165801525116
-0.548069953918457 -0.548069953918457
1.0625 -0.38718709349632263 -0.6011067032814026
-0.7151753902435303 -0.7151751518249512
0.9375 -0.305498868227005 -0.5303002595901489
-0.002231597900390625 -0.002231597900390625
1.0 -0.2681514620780945 -0.46994221210479736
-0.5859088897705078 -0.5859088897705078
1.125 -0.223882794380188 -0.4438254237174988
-0.9087028503417969 -0.9087021350860596
0.96875 -0.20104245841503143 -0.4390033185482025
-0.23839306831359863 -0.23839306831359863
1.09375 -0.24344903230667114 -0.398365318775177
-0.011393070220947266 -0.011393070220947266
1.03125 -0.2224387526512146 -0.4095136225223541
-0.37980198860168457 -0.37980222702026367
1.0 -0.2325950264930725 -0.38839951157569885
-0.5450496673583984 -0.5450491905212402
0.875 -0.32610833644866943 -0.5592808723449707
-0.5300545692443848 -0.530054569

-0.725379228591919 -0.7253789901733398
1.09375 -0.2275407761335373 -0.4881443977355957
-0.8461823463439941 -0.8461818695068359
1.0 -0.2781488299369812 -0.5360656380653381
-0.36949414014816284 -0.3694940507411957
0.96875 -0.2682788372039795 -0.4897979199886322
-0.04257631301879883 -0.04257631301879883
0.90625 -0.16645121574401855 -0.41345521807670593
-0.002170085906982422 -0.002170085906982422
0.90625 -0.21785825490951538 -0.43475833535194397
-0.010150432586669922 -0.010150432586669922
1.0 -0.1876055747270584 -0.46205559372901917
-0.8635832071304321 -0.863582968711853
1.03125 -0.23719002306461334 -0.47230881452560425
-0.3043088912963867 -0.3043088912963867
0.8125 -0.2447654902935028 -0.5051956176757812
-0.05678510665893555 -0.05678510665893555
0.8125 -0.25701865553855896 -0.48911142349243164
-0.03468036651611328 -0.03468036651611328
0.96875 -0.27105990052223206 -0.5039875507354736
-0.013565540313720703 -0.013565540313720703
0.6875 -0.23817047476768494 -0.5111532211303711
-0.001421928405

-1.3673779964447021 -1.367377758026123
0.78125 -0.2836316227912903 -0.5608454346656799
-0.3773193359375 -0.3773188591003418
0.96875 -0.29038006067276 -0.5379493832588196
-0.46616673469543457 -0.46616673469543457
0.90625 -0.14993494749069214 -0.3893093168735504
-0.03713035583496094 -0.03713035583496094
0.75 -0.21139979362487793 -0.49734270572662354
-0.6600894927978516 -0.6600890159606934
1.0625 -0.30261480808258057 -0.5508434772491455
-0.01225137710571289 -0.01225137710571289
1.21875 -0.19372782111167908 -0.4038078188896179
-0.14272260665893555 -0.14272260665893555
1.0 -0.25887733697891235 -0.526308000087738
-0.01889801025390625 -0.01889801025390625
1.03125 -0.26521167159080505 -0.5125712156295776
-0.1857929229736328 -0.1857929229736328
1.09375 -0.3028227984905243 -0.6480292081832886
-0.6189932823181152 -0.6189937591552734
1.0625 -0.3331320881843567 -0.6916289925575256
-0.9380857944488525 -0.9380857944488525
1.1875 -0.3221246600151062 -0.707359254360199
-0.7471146583557129 -0.7471146583

-0.25426244735717773 -0.25426244735717773
0.9375 -0.22372376918792725 -0.5108942985534668
-3.425048351287842 -3.425049066543579
1.125 -0.2820974588394165 -0.5904285311698914
-1.1800456047058105 -1.1800456047058105
1.0625 -0.3533965051174164 -0.6522685885429382
-2.157654285430908 -2.157654285430908
1.03125 -0.26436281204223633 -0.6079767942428589
-0.15406322479248047 -0.15406322479248047
0.84375 -0.30276334285736084 -0.5838996171951294
-0.557708740234375 -0.557708740234375
1.0625 -0.2487906962633133 -0.5386109352111816
-0.7075810432434082 -0.7075810432434082
0.78125 -0.260993093252182 -0.5472362041473389
-0.2688934803009033 -0.2688934803009033
0.84375 -0.2630058825016022 -0.5369086265563965
-0.4118967056274414 -0.4118967056274414
0.9375 -0.2496863603591919 -0.500839352607727
-0.2218034267425537 -0.2218036651611328
0.9375 -0.24471640586853027 -0.49442076683044434
-0.39548301696777344 -0.39548301696777344
0.8125 -0.22158697247505188 -0.4809194803237915
-0.163055419921875 -0.16305541992187

...

0.5625 -0.2784600853919983 -0.7010930180549622
-0.5893464088439941 -0.5893465280532837
0.625 -0.28574711084365845 -0.6175575256347656
-0.19028639793395996 -0.19028639793395996
0.6875 -0.35258787870407104 -0.7105873823165894
-1.4351706504821777 -1.4351706504821777
0.78125 -0.27221137285232544 -0.6514253616333008
-0.19184887409210205 -0.19184887409210205
0.5625 -0.24130111932754517 -0.6432149410247803
-0.3222919702529907 -0.32229185104370117
0.71875 -0.26428157091140747 -0.5611534118652344
-0.20640826225280762 -0.20640826225280762
0.6875 -0.23178809881210327 -0.5923879742622375
-1.6912784576416016 -1.6912782192230225
0.8125 -0.29596713185310364 -0.6494442820549011
-0.08985185623168945 -0.08985185623168945
0.75 -0.27008333802223206 -0.5703976154327393
-0.23758745193481445 -0.23758745193481445
0.84375 -0.28916436433792114 -0.6272844076156616
-0.15608739852905273 -0.15608739852905273
0.875 -0.3517002761363983 -0.6392984986305237
-0.15876269340515137 -0.15876269340515137
0.71875 -0.330159902

0.8125 -0.3332638144493103 -0.7219672799110413
-0.14407134056091309 -0.14407134056091309
0.59375 -0.3396627902984619 -0.6903741359710693
-0.20212721824645996 -0.20212697982788086
0.875 -0.37325966358184814 -0.6910473108291626
-0.14371562004089355 -0.14371562004089355
0.625 -0.29713186621665955 -0.6637330651283264
-1.402148723602295 -1.402148962020874
0.46875 -0.22844329476356506 -0.6402304768562317
-0.09121167659759521 -0.09121143817901611
0.75 -0.27481508255004883 -0.6396257281303406
-0.320725679397583 -0.320725679397583
0.5625 -0.25062382221221924 -0.6307791471481323
-0.13518691062927246 -0.13518691062927246
0.53125 -0.23807606101036072 -0.5955294370651245
-1.555260181427002 -1.5552600622177124
0.75 -0.2640158236026764 -0.6323868036270142
-0.26427340507507324 -0.26427340507507324
0.65625 -0.26190420985221863 -0.6382870674133301
-0.19185566902160645 -0.19185566902160645
0.75 -0.37017273902893066 -0.6536355018615723
-0.17274928092956543 -0.17274928092956543
0.75 -0.2653481364250183 -0.

0.59375 -0.26486936211586 -0.5788918137550354
-0.3541889190673828 -0.3541889190673828
0.75 -0.27597787976264954 -0.5954815149307251
-0.4523240327835083 -0.45232415199279785
0.6875 -0.28548136353492737 -0.6518502235412598
-0.2109062671661377 -0.2109062671661377
0.71875 -0.3088919222354889 -0.6585698127746582
-0.18634438514709473 -0.18634438514709473
0.6875 -0.26318231225013733 -0.6255180239677429
-0.2251894474029541 -0.2251894474029541
0.78125 -0.3343488574028015 -0.6291582584381104
-0.30735278129577637 -0.30735278129577637
0.6875 -0.3020419180393219 -0.6518241763114929
-0.46860432624816895 -0.46860432624816895
0.84375 -0.26343345642089844 -0.6655170917510986
-0.19785404205322266 -0.19785404205322266
0.625 -0.3092881739139557 -0.6503099203109741
-0.19091176986694336 -0.19091176986694336
0.65625 -0.3255636990070343 -0.6535806059837341
-0.20162248611450195 -0.20162248611450195
0.84375 -0.3762836456298828 -0.6495879292488098
-0.31891727447509766 -0.3189173936843872
0.6875 -0.33205533027648

0.6875 -0.2846979796886444 -0.6533001065254211
-0.1303267478942871 -0.1303267478942871
0.78125 -0.2827145457267761 -0.662786066532135
-0.21376490592956543 -0.21376490592956543
0.6875 -0.27149975299835205 -0.6827569007873535
-3.543994426727295 -3.543994426727295
0.75 -0.2879681885242462 -0.635953962802887
-0.19688868522644043 -0.19688868522644043
0.65625 -0.27814698219299316 -0.6592127680778503
-0.20709967613220215 -0.20709943771362305
0.78125 -0.2864164113998413 -0.6539294123649597
-0.18461990356445312 -0.18461990356445312
0.71875 -0.28200697898864746 -0.6586122512817383
-0.16757559776306152 -0.16757559776306152
0.59375 -0.22013767063617706 -0.6553711295127869
-0.22875547409057617 -0.22875571250915527
0.5625 -0.2962191700935364 -0.6944872140884399
-2.4915544986724854 -2.4915542602539062
0.625 -0.28756242990493774 -0.7167859673500061
-1.5283427238464355 -1.5283424854278564
0.53125 -0.29164808988571167 -0.6957786679267883
-0.29303956031799316 -0.29303956031799316
0.5625 -0.25625288486480

0.8125 -0.29294151067733765 -0.6987830400466919
-0.22413134574890137 -0.22413134574890137
0.75 -0.3179607391357422 -0.6561800241470337
-0.2064039707183838 -0.2064039707183838
0.65625 -0.2778822183609009 -0.6624200344085693
-0.2317960262298584 -0.2317962646484375
0.75 -0.34477299451828003 -0.6960208415985107
-0.30458974838256836 -0.3045898675918579
0.59375 -0.32660287618637085 -0.6758075952529907
-1.6735153198242188 -1.6735155582427979
0.625 -0.2743600308895111 -0.6616992354393005
-0.7808947563171387 -0.7808952331542969
0.8125 -0.24689538776874542 -0.6267037987709045
-1.3805418014526367 -1.3805420398712158
0.59375 -0.2332746684551239 -0.6018257141113281
-1.962165117263794 -1.962165355682373
0.78125 -0.34449565410614014 -0.6517845392227173
-0.25533103942871094 -0.25533127784729004
0.625 -0.29162031412124634 -0.6508008241653442
-0.6457776427268982 -0.6457775831222534
0.625 -0.2901775538921356 -0.6438093185424805
-0.5218589901924133 -0.5218589305877686
0.625 -0.3119487166404724 -0.64055240

In [ ]:
train() #greedy binary clipped positive weighted clipped negative reinforcement #no decoder layers

1.3125 -1.708974838256836 -1.7904541492462158 -1.6757166385650635 -1.6757166385650635
1.21875 -1.5634243488311768 -1.758994698524475 -1.7462409734725952 -1.7462407350540161
1.375 -1.5086345672607422 -1.7554669380187988 -1.8359782695770264 -1.8359780311584473
1.03125 -1.3636950254440308 -1.720251202583313 -1.3886760473251343 -1.3886761665344238
0.96875 -1.1558616161346436 -1.5697258710861206 -2.7289011478424072 -2.7289011478424072
0.78125 -0.883027195930481 -1.382416844367981 -0.48224011063575745 -0.48224011063575745
1.1875 -0.5622961521148682 -0.9680682420730591 -0.7630823850631714 -0.7630821466445923
1.21875 -0.6196686029434204 -0.9888993501663208 -1.0976417064666748 -1.0976420640945435
0.875 -0.8124260306358337 -1.1171694993972778 -0.6871669292449951 -0.6871674060821533
1.1875 -0.5238097906112671 -0.8430900573730469 -0.38819265365600586 -0.38819265365600586
1.40625 -0.40508437156677246 -0.7490813732147217 -0.11362004280090332 -0.11362004280090332
1.125 -0.46553540229797363 -0.7949967

1.0625 -0.2812857925891876 -0.5377365350723267 -2.7916259765625 -2.7916252613067627
1.15625 -0.30035150051116943 -0.5253403186798096 -0.6283981800079346 -0.6283984184265137
0.90625 -0.20373263955116272 -0.4023823142051697 -0.021153688430786133 -0.021153688430786133
1.125 -0.38167476654052734 -0.6229497790336609 -0.4799180030822754 -0.4799177646636963
0.90625 -0.24691255390644073 -0.5038642883300781 -1.283452033996582 -1.283452033996582
1.0625 -0.31190675497055054 -0.5640049576759338 -0.03444027900695801 -0.03444027900695801
0.84375 -0.2628597915172577 -0.48793506622314453 -0.4391517639160156 -0.43915224075317383
1.125 -0.1920265257358551 -0.3965808153152466 -0.003968238830566406 -0.003968238830566406
0.9375 -0.2032368779182434 -0.39308300614356995 -0.09795475006103516 -0.09795522689819336
0.96875 -0.22173194587230682 -0.37321794033050537 -0.44632816314697266 -0.44632816314697266
0.96875 -0.15283039212226868 -0.28760048747062683 -0.07139420509338379 -0.07139420509338379
0.90625 -0.20844

1.0 -0.2180393934249878 -0.44354483485221863 -0.21612560749053955 -0.21612548828125
0.9375 -0.24085037410259247 -0.47802799940109253 -0.05118405818939209 -0.05118405818939209
1.03125 -0.18930666148662567 -0.4870046377182007 -0.23678624629974365 -0.23678624629974365
1.15625 -0.22320301830768585 -0.4860403835773468 -0.22089087963104248 -0.22089135646820068
1.03125 -0.34373927116394043 -0.69587242603302 -1.2328810691833496 -1.2328813076019287
1.15625 -0.3686874508857727 -0.685194194316864 -0.6479103565216064 -0.6479103565216064
0.90625 -0.27051693201065063 -0.5809031128883362 -2.048229932785034 -2.0482301712036133
1.15625 -0.2752707004547119 -0.5671423673629761 -0.02338576316833496 -0.02338552474975586
1.0625 -0.24723659455776215 -0.5515410900115967 -0.975777268409729 -0.975777268409729
1.0 -0.25050413608551025 -0.537704348564148 -0.32361936569213867 -0.32361912727355957
0.96875 -0.28098973631858826 -0.5665231347084045 -0.043975114822387695 -0.043975114822387695
1.0625 -0.3022069334983825

0.8125 -0.1997504085302353 -0.47223761677742004 -2.575652599334717 -2.5756521224975586
0.9375 -0.2261885404586792 -0.5151216983795166 -0.15795469284057617 -0.15795469284057617
1.0 -0.18397459387779236 -0.5353063941001892 -0.2780252695083618 -0.27802515029907227
1.15625 -0.23263192176818848 -0.5685824751853943 -0.16706061363220215 -0.16706061363220215
0.78125 -0.22833847999572754 -0.541318416595459 -0.1228790283203125 -0.1228790283203125
0.75 -0.2573418617248535 -0.5933953523635864 -3.4080488681793213 -3.4080488681793213
0.71875 -0.19637948274612427 -0.5201794505119324 -0.2362256646156311 -0.2362256646156311
1.0 -0.23829714953899384 -0.5446258187294006 -0.0658411979675293 -0.0658411979675293
0.96875 -0.2703506648540497 -0.4993382692337036 -0.8064103126525879 -0.8064103126525879
0.875 -0.22191521525382996 -0.5695966482162476 -3.0231430530548096 -3.0231428146362305
1.0 -0.24818074703216553 -0.6216410994529724 -0.16316866874694824 -0.1631685495376587
0.6875 -0.4008658230304718 -0.851638376

0.90625 -0.2782413959503174 -0.5696936845779419 -0.16750609874725342 -0.16750609874725342
0.90625 -0.2390444427728653 -0.5323607325553894 -0.21147990226745605 -0.21147966384887695
1.0625 -0.268923282623291 -0.6621469855308533 -0.12210702896118164 -0.12210702896118164
0.9375 -0.38655751943588257 -0.7659754753112793 -0.32547831535339355 -0.32547831535339355
1.125 -0.34922105073928833 -0.7334529757499695 -2.3410251140594482 -2.3410253524780273
0.875 -0.18738029897212982 -0.4683200716972351 -0.1669936180114746 -0.16699433326721191
1.0 -0.12097181379795074 -0.3565872609615326 -0.12420022487640381 -0.12420022487640381
0.8125 -0.09162445366382599 -0.2767462134361267 -0.019463062286376953 -0.019463062286376953
0.75 -0.15989699959754944 -0.3700137734413147 -0.03265810012817383 -0.03265810012817383
0.875 -0.11888202279806137 -0.29765239357948303 -0.008105754852294922 -0.008105278015136719
0.78125 -0.07840772718191147 -0.21630439162254333 -0.005907535552978516 -0.005907535552978516
0.96875 -0.153

...

0.8125 -0.23217226564884186 -0.6341050267219543 -0.20882225036621094 -0.20882225036621094
1.0625 -0.2506090998649597 -0.6720247864723206 -0.19559311866760254 -0.19559311866760254
0.90625 -0.21289581060409546 -0.6324797868728638 -0.2319507598876953 -0.2319507598876953
0.96875 -0.2220359742641449 -0.6494190096855164 -0.1394033432006836 -0.1394033432006836
0.90625 -0.2808643579483032 -0.6842454075813293 -2.322136163711548 -2.322136402130127
0.84375 -0.29091763496398926 -0.7059842348098755 -0.3888993263244629 -0.38889938592910767
0.875 -0.22728665173053741 -0.6438489556312561 -0.2220780849456787 -0.2220780849456787
0.71875 -0.2415771782398224 -0.6296600103378296 -0.20392584800720215 -0.20392584800720215
0.875 -0.27228623628616333 -0.6593730449676514 -0.14777898788452148 -0.14777898788452148
0.6875 -0.21601715683937073 -0.5994625687599182 -0.18014097213745117 -0.18014097213745117
1.0625 -0.25467997789382935 -0.6431596875190735 -0.1742323637008667 -0.1742323637008667
0.875 -0.232943385839462

0.96875 -0.22550924122333527 -0.5789922475814819 -0.14342808723449707 -0.14342808723449707
1.09375 -0.23394440114498138 -0.6510211229324341 -1.7508180141448975 -1.7508180141448975
0.6875 -0.22122403979301453 -0.6953940391540527 -2.1936261653900146 -2.1936264038085938
0.84375 -0.27396583557128906 -0.7047908306121826 -0.22257232666015625 -0.22257232666015625
0.96875 -0.2751571834087372 -0.6953544616699219 -0.4080491065979004 -0.4080491065979004
1.0 -0.2375771850347519 -0.6853095889091492 -0.19987010955810547 -0.19987010955810547
1.03125 -0.2494300752878189 -0.6745315194129944 -0.22776222229003906 -0.22776222229003906
0.90625 -0.2444687783718109 -0.6729321479797363 -0.28647875785827637 -0.28647851943969727
0.8125 -0.2599842846393585 -0.6905440092086792 -0.23333501815795898 -0.23333501815795898
0.96875 -0.2263142615556717 -0.6290341019630432 -0.19501662254333496 -0.19501662254333496
0.75 -0.22740903496742249 -0.6492998003959656 -2.112443685531616 -2.1124439239501953
0.90625 -0.232061892747

0.8125 -0.27601903676986694 -0.6445903182029724 -0.1844080686569214 -0.1844080686569214
0.6875 -0.24528177082538605 -0.6650682687759399 -0.16614151000976562 -0.16614151000976562
0.71875 -0.19954757392406464 -0.6116915345191956 -0.5165862441062927 -0.5165864825248718
0.9375 -0.2027476727962494 -0.6086918115615845 -0.19952726364135742 -0.19952726364135742
1.03125 -0.22125083208084106 -0.6521191000938416 -0.3196863532066345 -0.3196863532066345
1.03125 -0.2123524248600006 -0.5823129415512085 -0.1877901554107666 -0.1877901554107666
0.8125 -0.2091606855392456 -0.631300151348114 -1.9419220685958862 -1.9419219493865967
0.6875 -0.2456800639629364 -0.6837382316589355 -1.999590516090393 -1.999590277671814
0.78125 -0.21281158924102783 -0.6450124382972717 -0.2179884910583496 -0.2179887294769287
0.78125 -0.23993979394435883 -0.6488995552062988 -0.2413027286529541 -0.2413027286529541
0.78125 -0.25775080919265747 -0.675859272480011 -0.15676534175872803 -0.15676534175872803
0.84375 -0.23183736205101013

0.90625 -0.26158255338668823 -0.660051167011261 -0.17383527755737305 -0.17383503913879395
0.90625 -0.29694950580596924 -0.6618273258209229 -0.1646718978881836 -0.1646718978881836
0.8125 -0.22012954950332642 -0.5832209587097168 -0.16353273391723633 -0.16353273391723633
0.96875 -0.2277577966451645 -0.6541529297828674 -0.374190092086792 -0.374190092086792
0.78125 -0.23290997743606567 -0.6203783750534058 -0.3821800947189331 -0.3821800947189331
0.90625 -0.22237107157707214 -0.6495550870895386 -2.157850980758667 -2.157850742340088
0.6875 -0.23825019598007202 -0.6929165124893188 -0.24334406852722168 -0.24334406852722168
0.9375 -0.3039360046386719 -0.669169008731842 -0.18008089065551758 -0.18008065223693848
0.90625 -0.22465580701828003 -0.6191229820251465 -0.21409082412719727 -0.21409082412719727
0.875 -0.20089316368103027 -0.6126549243927002 -0.17642617225646973 -0.17642617225646973
0.84375 -0.19147929549217224 -0.60237717628479 -0.14707565307617188 -0.14707565307617188
0.9375 -0.297819674015

0.96875 -0.23746711015701294 -0.6448031067848206 -2.0229544639587402 -2.0229544639587402
1.125 -0.21424183249473572 -0.6546593308448792 -0.17508888244628906 -0.17508888244628906
0.875 -0.2087438851594925 -0.6220215559005737 -0.18991422653198242 -0.18991422653198242
0.75 -0.2384210228919983 -0.6046275496482849 -0.2441248893737793 -0.2441248893737793
0.6875 -0.2049161195755005 -0.5977683067321777 -0.20683932304382324 -0.20683932304382324
0.875 -0.21660025417804718 -0.6056616902351379 -0.14450311660766602 -0.14450311660766602
0.75 -0.2444373220205307 -0.6456263661384583 -0.22050678730010986 -0.2205066680908203
0.75 -0.25408366322517395 -0.6998106837272644 -0.16391503810882568 -0.16391491889953613
0.84375 -0.26466214656829834 -0.6883446574211121 -0.294217586517334 -0.294217586517334


In [ ]:
train() #greedy clipped weighted reinforcement #no decoder layers #FUCKING HELL!!!!!!!!!!!!!!!!!!!!!

1.21875 -1.6955313682556152 -1.7862424850463867 -1.8639683723449707 -1.8639682531356812
1.21875 -1.5781826972961426 -1.779500126838684 -1.9546620845794678 -1.9546620845794678
1.125 -1.3864039182662964 -1.723914623260498 -2.2866005897521973 -2.2866005897521973
1.0625 -1.4572614431381226 -1.7373807430267334 -2.0887045860290527 -2.088704824447632
1.15625 -1.4872794151306152 -1.7522391080856323 -1.6916835308074951 -1.6916835308074951
1.03125 -1.4814026355743408 -1.7484896183013916 -1.6586461067199707 -1.6586461067199707
1.125 -1.4968632459640503 -1.7524878978729248 -1.5371580123901367 -1.5371578931808472
1.09375 -1.3820888996124268 -1.719040036201477 -1.5088753700256348 -1.5088753700256348
1.3125 -1.469407558441162 -1.7382795810699463 -1.5583242177963257 -1.5583243370056152
1.09375 -1.4794856309890747 -1.75258469581604 -2.355281352996826 -2.355281352996826
1.0625 -1.4835776090621948 -1.7522817850112915 -1.4801610708236694 -1.480161190032959
1.15625 -1.5176492929458618 -1.7555623054504395 -

0.96875 -1.1755969524383545 -1.6927316188812256 -2.3397035598754883 -2.3397035598754883
0.90625 -1.0957777500152588 -1.6666582822799683 -0.7530695199966431 -0.7530695199966431
1.03125 -1.2653732299804688 -1.7120031118392944 -1.0376248359680176 -1.0376248359680176
1.03125 -1.2900559902191162 -1.7194063663482666 -1.887976050376892 -1.887975811958313
1.0 -1.2529535293579102 -1.7221941947937012 -0.9255737066268921 -0.9255735874176025
0.875 -1.2049680948257446 -1.7061126232147217 -1.8996291160583496 -1.8996292352676392
0.96875 -1.1985373497009277 -1.7106724977493286 -2.141012668609619 -2.14101243019104
0.6875 -1.0914790630340576 -1.6660181283950806 -1.7568397521972656 -1.7568398714065552
0.78125 -1.149078607559204 -1.6922208070755005 -1.278857946395874 -1.278857946395874
0.75 -1.1619439125061035 -1.6908756494522095 -2.1164591312408447 -2.1164591312408447
0.84375 -1.299497127532959 -1.7280091047286987 -2.028010606765747 -2.028010606765747
0.875 -1.223714828491211 -1.712692141532898 -2.115571

0.875 -1.1722267866134644 -1.6886398792266846 -1.4389801025390625 -1.4389801025390625
1.03125 -1.1992261409759521 -1.7116931676864624 -1.4153614044189453 -1.4153615236282349
0.8125 -1.157042384147644 -1.683106780052185 -2.0137526988983154 -2.0137526988983154
1.03125 -1.108180046081543 -1.6951680183410645 -2.2002809047698975 -2.2002809047698975
1.03125 -1.1873369216918945 -1.7009186744689941 -1.0679949522018433 -1.0679949522018433
0.9375 -1.2465323209762573 -1.719456672668457 -1.11089026927948 -1.11089026927948
0.8125 -1.3161323070526123 -1.7286971807479858 -1.4638335704803467 -1.4638335704803467
0.84375 -1.2761658430099487 -1.7312920093536377 -2.013118028640747 -2.013118028640747
0.84375 -1.125045657157898 -1.6718593835830688 -1.194845199584961 -1.194845199584961
1.0 -1.1571379899978638 -1.6885699033737183 -2.1477136611938477 -2.1477136611938477
0.875 -1.1429047584533691 -1.692136526107788 -2.113433599472046 -2.113433599472046
0.84375 -1.1747289896011353 -1.6915432214736938 -1.14529860

0.96875 -1.158735752105713 -1.673050045967102 -2.150857448577881 -2.150857448577881
1.1875 -1.1981143951416016 -1.7022892236709595 -2.232435703277588 -2.232435941696167
0.96875 -1.2220385074615479 -1.7044681310653687 -1.944463849067688 -1.9444637298583984
0.6875 -1.1834179162979126 -1.7128932476043701 -1.904757022857666 -1.9047572612762451
0.8125 -1.20729660987854 -1.7091538906097412 -1.5122885704040527 -1.5122885704040527
0.8125 -1.1317237615585327 -1.698191523551941 -2.098644495010376 -2.098644256591797
1.03125 -1.0470333099365234 -1.6414891481399536 -0.7996473908424377 -0.7996473908424377
0.71875 -1.0711405277252197 -1.6577316522598267 -2.109318256378174 -2.109318256378174
0.6875 -1.0835634469985962 -1.65263032913208 -2.1513280868530273 -2.1513280868530273
0.8125 -0.993277370929718 -1.633302927017212 -0.6484153866767883 -0.6484153866767883
0.875 -1.031132459640503 -1.6543049812316895 -1.8675258159637451 -1.8675258159637451
0.90625 -1.0171828269958496 -1.6524299383163452 -1.923686742

0.84375 -1.0289591550827026 -1.6575944423675537 -1.0806673765182495 -1.08066725730896
0.78125 -1.0765740871429443 -1.6697334051132202 -1.0578159093856812 -1.0578157901763916
0.625 -1.0807551145553589 -1.669901728630066 -0.8097611665725708 -0.8097612261772156
0.78125 -1.0834619998931885 -1.6431410312652588 -2.0978646278381348 -2.097864866256714
0.8125 -1.0438872575759888 -1.658522129058838 -0.911722719669342 -0.911722719669342
0.84375 -1.1800472736358643 -1.6840274333953857 -1.5362855195999146 -1.536285638809204
0.84375 -1.0974904298782349 -1.6682398319244385 -1.9784939289093018 -1.9784939289093018
0.78125 -1.132115125656128 -1.6930968761444092 -2.1579833030700684 -2.1579833030700684
0.625 -1.099245548248291 -1.6663546562194824 -0.7529283761978149 -0.7529283761978149
0.75 -1.135243535041809 -1.689098596572876 -2.0773491859436035 -2.0773491859436035
0.875 -1.1099927425384521 -1.7097749710083008 -1.9666963815689087 -1.9666963815689087
0.90625 -1.1771808862686157 -1.6906754970550537 -1.407

...

0.71875 -0.7789806127548218 -1.541504979133606 -0.6089456081390381 -0.6089456677436829
0.65625 -0.8151389956474304 -1.5375244617462158 -2.070830821990967 -2.0708305835723877
0.53125 -0.7894154787063599 -1.5369263887405396 -0.46974027156829834 -0.46974027156829834
0.59375 -0.8265954256057739 -1.542956829071045 -0.484012246131897 -0.4840123653411865
0.6875 -0.8334065675735474 -1.5756255388259888 -2.1849210262298584 -2.1849210262298584
0.71875 -0.9116613864898682 -1.5868514776229858 -2.145068645477295 -2.145068407058716
0.5 -0.7625278234481812 -1.5459606647491455 -0.8711429834365845 -0.8711429238319397
0.625 -0.8524677157402039 -1.5680115222930908 -1.1727392673492432 -1.1727392673492432
0.625 -0.9309703707695007 -1.5632967948913574 -2.160325050354004 -2.160325050354004
0.65625 -0.8002182245254517 -1.5865675210952759 -2.2186543941497803 -2.2186543941497803
0.625 -0.8533756732940674 -1.5448147058486938 -0.5205358266830444 -0.520535945892334
0.59375 -0.8680099248886108 -1.5316969156265259 -2

0.5625 -0.8053420186042786 -1.521944284439087 -2.1879348754882812 -2.1879351139068604
0.625 -0.81699138879776 -1.52406907081604 -0.8211853504180908 -0.8211855292320251
0.4375 -0.9317924380302429 -1.568147897720337 -0.9430571794509888 -0.9430571794509888
0.5 -0.836301863193512 -1.5842126607894897 -0.5388306379318237 -0.5388306379318237
0.6875 -0.9176725149154663 -1.5580165386199951 -2.1193864345550537 -2.119386672973633
0.6875 -0.8360683917999268 -1.5575494766235352 -0.7831480503082275 -0.7831480503082275
0.53125 -0.7838382720947266 -1.517887830734253 -1.8076529502868652 -1.8076529502868652
0.46875 -0.9210155010223389 -1.6000709533691406 -1.9487881660461426 -1.9487881660461426
0.4375 -0.8462563753128052 -1.5514001846313477 -2.5278120040893555 -2.5278120040893555
0.75 -0.818912148475647 -1.5700052976608276 -0.6833518147468567 -0.6833518147468567
0.65625 -0.86312335729599 -1.5481504201889038 -1.0466930866241455 -1.0466930866241455
0.5 -0.9151152968406677 -1.5898232460021973 -1.61974835395

0.5625 -0.8901995420455933 -1.5732474327087402 -0.6457995176315308 -0.6457993984222412
0.4375 -0.8003426790237427 -1.549799919128418 -0.5678775310516357 -0.567877471446991
0.5625 -0.9371176958084106 -1.6064733266830444 -2.0849101543426514 -2.0849101543426514
0.71875 -0.9499279260635376 -1.60305917263031 -1.7796711921691895 -1.7796710729599
0.6875 -0.8789063692092896 -1.579749584197998 -0.751468300819397 -0.7514681816101074
0.5625 -0.8768534660339355 -1.5964912176132202 -0.985194206237793 -0.9851940870285034
0.59375 -0.9013004899024963 -1.641913890838623 -2.3205623626708984 -2.3205621242523193
0.5625 -0.9776128530502319 -1.6161359548568726 -2.0892493724823 -2.0892493724823
0.71875 -0.9805776476860046 -1.655315637588501 -0.6893554925918579 -0.6893556118011475
0.71875 -1.0267506837844849 -1.647950291633606 -2.0302207469940186 -2.0302207469940186
0.53125 -0.9507981538772583 -1.6441233158111572 -0.941498875617981 -0.9414988160133362
0.6875 -0.9676979184150696 -1.616133213043213 -2.364781856

0.59375 -0.9022669196128845 -1.6136057376861572 -2.1488261222839355 -2.1488261222839355
0.78125 -0.9499257802963257 -1.6301915645599365 -0.8011879920959473 -0.8011881709098816
0.625 -0.8456485867500305 -1.5870667695999146 -2.1344029903411865 -2.1344027519226074
0.65625 -0.939631462097168 -1.610244631767273 -0.7891145348548889 -0.7891144156455994
0.53125 -0.9153868556022644 -1.6061913967132568 -0.7457191944122314 -0.7457192540168762
0.71875 -0.8974065184593201 -1.6033928394317627 -2.293104648590088 -2.293104410171509
0.625 -0.9917762279510498 -1.6212221384048462 -2.1636149883270264 -2.1636149883270264
0.46875 -0.9611546993255615 -1.629752278327942 -0.8420872092247009 -0.8420871496200562
0.5625 -0.8783262968063354 -1.5947790145874023 -2.045856475830078 -2.045856475830078
0.46875 -0.9548653960227966 -1.6472976207733154 -2.070864200592041 -2.070864200592041
0.71875 -0.9917577505111694 -1.6678720712661743 -0.8186939358711243 -0.8186937570571899
0.65625 -0.9632092714309692 -1.642438888549804

0.5 -0.849945604801178 -1.547255277633667 -2.1740994453430176 -2.1740994453430176
0.53125 -0.7657721042633057 -1.5200738906860352 -2.1234893798828125 -2.1234893798828125
0.71875 -0.8605554103851318 -1.5636025667190552 -0.968632161617279 -0.968632161617279
0.59375 -0.7961407899856567 -1.5534412860870361 -2.1689634323120117 -2.1689634323120117
0.53125 -0.8808479309082031 -1.5765835046768188 -0.7049918174743652 -0.7049919366836548
0.71875 -0.9084848165512085 -1.5933457612991333 -2.2673983573913574 -2.2673983573913574
0.71875 -0.9109517931938171 -1.614391803741455 -0.7073957920074463 -0.7073956727981567
0.6875 -0.8720791339874268 -1.5559751987457275 -0.7193743586540222 -0.719374418258667
0.53125 -0.895416259765625 -1.5810132026672363 -0.83888840675354 -0.83888840675354
0.5 -0.8432275056838989 -1.5823695659637451 -1.3736042976379395 -1.373604416847229
0.46875 -0.79362952709198 -1.5451867580413818 -0.6804370880126953 -0.6804370880126953
0.625 -0.8999744653701782 -1.5778357982635498 -0.751261

In [2]:
train() #5 points (same architecture as above), change cutoff to -5

3.625 -4.613802909851074 -4.7838850021362305 -4.8107404708862305 -4.8107404708862305
4.0625 -4.548521518707275 -4.777702331542969 -4.748869895935059 -4.748869895935059
4.0 -4.459712505340576 -4.772681713104248 -5.060706615447998 -5.060707092285156
3.65625 -4.193982124328613 -4.713046550750732 -4.500046730041504 -4.500046730041504
3.78125 -4.323950290679932 -4.747553825378418 -4.627432823181152 -4.627432823181152
3.0 -4.445315361022949 -4.7676801681518555 -4.650610446929932 -4.650610446929932
3.53125 -4.527420997619629 -4.774611473083496 -4.551832675933838 -4.551832675933838
3.65625 -4.56427526473999 -4.777422904968262 -4.950989246368408 -4.950989246368408
3.625 -4.515145301818848 -4.779849529266357 -4.6244401931762695 -4.6244401931762695
3.4375 -4.494828224182129 -4.776103973388672 -4.677218437194824 -4.677218437194824
3.6875 -4.485567569732666 -4.780467510223389 -4.734873294830322 -4.734873294830322
3.1875 -4.483242034912109 -4.776390075683594 -4.881979942321777 -4.881979942321777
3.4

3.53125 -4.224320411682129 -4.741398334503174 -4.898557186126709 -4.898556709289551
3.46875 -4.1890363693237305 -4.73051118850708 -4.993677139282227 -4.993677139282227
3.375 -4.177962303161621 -4.7416863441467285 -5.032142162322998 -5.032142162322998
3.40625 -4.1776227951049805 -4.735321521759033 -5.001372337341309 -5.00137186050415
3.0625 -4.170699119567871 -4.737248420715332 -5.0162224769592285 -5.016222953796387
3.46875 -4.2523956298828125 -4.740450382232666 -4.922818183898926 -4.922817707061768
3.4375 -4.147514343261719 -4.741376876831055 -4.905962944030762 -4.905962944030762
3.09375 -4.15795373916626 -4.712965488433838 -5.261414527893066 -5.261414527893066
3.3125 -4.158411979675293 -4.736183166503906 -5.009368896484375 -5.009368419647217
3.4375 -4.132844924926758 -4.724868297576904 -4.942559242248535 -4.942559242248535
3.1875 -4.146387100219727 -4.729586124420166 -4.992178440093994 -4.992178440093994
3.6875 -4.145415306091309 -4.724677562713623 -5.084786415100098 -5.08478641510009

2.78125 -4.182097434997559 -4.731659889221191 -5.08526611328125 -5.08526611328125
3.6875 -4.2018585205078125 -4.740363597869873 -5.034965515136719 -5.034965515136719
3.46875 -4.239253997802734 -4.738203048706055 -4.277524948120117 -4.277524948120117
3.46875 -4.215435981750488 -4.736764430999756 -4.462321758270264 -4.4623212814331055
3.34375 -4.213251113891602 -4.730818271636963 -4.452569484710693 -4.452569007873535
3.28125 -4.146288871765137 -4.726629734039307 -5.011261940002441 -5.0112624168396
2.90625 -4.143773078918457 -4.710502624511719 -4.847438812255859 -4.847438812255859
2.78125 -4.140874862670898 -4.732651233673096 -5.083136558532715 -5.083136558532715
3.3125 -4.218873023986816 -4.74692964553833 -4.419147491455078 -4.41914701461792
3.1875 -4.272647857666016 -4.73798131942749 -5.132097244262695 -5.132096767425537
3.3125 -4.208124160766602 -4.738154411315918 -5.063543796539307 -5.063543796539307
3.21875 -4.168090343475342 -4.73468017578125 -4.643953800201416 -4.643953800201416
3.

3.125 -4.140661716461182 -4.7113542556762695 -4.975409984588623 -4.975409984588623
3.0625 -4.168606758117676 -4.725063323974609 -4.763280868530273 -4.763280868530273
3.125 -4.161951065063477 -4.728622913360596 -4.898269176483154 -4.898269176483154
3.3125 -4.18517541885376 -4.734040260314941 -4.996801376342773 -4.996801376342773
3.5 -4.2149505615234375 -4.730482578277588 -4.099761962890625 -4.099761962890625
3.3125 -4.166631698608398 -4.724865913391113 -4.167041778564453 -4.167041778564453
3.40625 -4.166460037231445 -4.729261875152588 -5.051675796508789 -5.051675796508789
3.3125 -4.181024551391602 -4.729369163513184 -4.267481803894043 -4.267481803894043
3.34375 -4.187760353088379 -4.729628562927246 -4.874156951904297 -4.874156951904297
2.96875 -4.212619781494141 -4.731738567352295 -4.761923789978027 -4.761923789978027
3.21875 -4.263606071472168 -4.74923038482666 -4.938270092010498 -4.938270092010498
2.875 -4.235060691833496 -4.746899127960205 -5.013260841369629 -5.013260841369629
2.9375

3.3125 -4.153008460998535 -4.740481853485107 -4.6927971839904785 -4.6927971839904785
3.125 -4.097817420959473 -4.699760913848877 -5.002999305725098 -5.002999305725098
3.0 -4.118674278259277 -4.704927444458008 -4.1927809715271 -4.192781448364258
3.375 -4.164780616760254 -4.74321174621582 -4.984238147735596 -4.984238624572754
2.96875 -4.220085144042969 -4.730958461761475 -4.966148376464844 -4.966148376464844
3.21875 -4.221129417419434 -4.745389938354492 -5.012149333953857 -5.012148857116699
3.0 -4.184775352478027 -4.735687255859375 -4.986310958862305 -4.986310958862305
3.21875 -4.210723400115967 -4.7370781898498535 -4.931967258453369 -4.931967258453369
3.03125 -4.1461591720581055 -4.732954978942871 -4.083438873291016 -4.083438873291016
3.4375 -4.1337456703186035 -4.720108509063721 -4.570761680603027 -4.570761680603027
3.25 -4.147449493408203 -4.7300519943237305 -4.118678092956543 -4.118678092956543
2.96875 -4.160475254058838 -4.707831859588623 -4.163566589355469 -4.163566589355469
3.1562

...

2.0 -0.20408716797828674 -0.40801507234573364 -0.002415776252746582 -0.002415776252746582
2.15625 -0.2144116461277008 -0.4008694589138031 -0.6898131370544434 -0.6898131370544434
2.3125 -0.22569547593593597 -0.32944419980049133 -0.6202516555786133 -0.6202511787414551
2.125 -0.20204441249370575 -0.36929643154144287 -0.0018777847290039062 -0.0018777847290039062
2.28125 -0.17958715558052063 -0.3275226056575775 -0.008322954177856445 -0.008322954177856445
2.34375 -0.2754579186439514 -0.40695175528526306 -0.09681272506713867 -0.09681272506713867
2.21875 -0.1936422884464264 -0.3775903284549713 -0.009302854537963867 -0.009302854537963867
2.3125 -0.16613885760307312 -0.38699957728385925 -0.6276280879974365 -0.6276278495788574
2.1875 -0.20365841686725616 -0.3900291323661804 -0.0540776252746582 -0.0540776252746582
2.34375 -0.2157825529575348 -0.3862074911594391 -0.4020850658416748 -0.4020850658416748
2.125 -0.25375795364379883 -0.4805324673652649 -0.06182277202606201 -0.06182277202606201
2.28125 -

2.21875 -0.16988897323608398 -0.3619828522205353 -1.5203185081481934 -1.5203194618225098
2.09375 -0.19918635487556458 -0.4178790748119354 -0.007793903350830078 -0.007793903350830078
2.3125 -0.22942641377449036 -0.38745883107185364 -0.29633522033691406 -0.29633522033691406
2.0 -0.15196003019809723 -0.37834274768829346 -0.4116687774658203 -0.4116687774658203
2.21875 -0.16276328265666962 -0.3320215046405792 -0.2620565891265869 -0.2620565891265869
2.34375 -0.2604406476020813 -0.49237948656082153 -0.00018262863159179688 -0.00018262863159179688
2.0625 -0.1389927864074707 -0.375552773475647 -0.17864561080932617 -0.17864561080932617
2.25 -0.209411159157753 -0.3953971564769745 -0.8210577964782715 -0.8210573196411133
2.375 -0.1862505078315735 -0.3626387417316437 -0.8139162063598633 -0.8139164447784424
2.21875 -0.22614791989326477 -0.36486682295799255 -0.028925418853759766 -0.028925418853759766
2.46875 -0.16863049566745758 -0.3140753507614136 -0.18751955032348633 -0.18751955032348633
2.40625 -0.2

2.21875 -0.27386409044265747 -0.5418379902839661 -1.0411877632141113 -1.0411889553070068
2.46875 -0.1647462397813797 -0.4339633882045746 -0.2077641487121582 -0.2077641487121582
1.9375 -0.19518586993217468 -0.3933241665363312 -2.2279043197631836 -2.2279038429260254
2.03125 -0.18786516785621643 -0.42071792483329773 -0.28360724449157715 -0.28360629081726074
2.28125 -0.300422340631485 -0.40635040402412415 -0.6230707168579102 -0.623070240020752
1.96875 -0.08444300293922424 -0.43557965755462646 -1.157564640045166 -1.157564640045166
2.0625 -0.1839148998260498 -0.42660290002822876 -0.027626939117908478 -0.027626939117908478
1.78125 -0.24789856374263763 -0.4379381835460663 -0.15008974075317383 -0.15008997917175293
2.125 -0.1814108043909073 -0.4346221387386322 -0.4705672264099121 -0.4705672264099121
2.1875 -0.1570044755935669 -0.46124467253685 -0.015799880027770996 -0.015799880027770996
2.1875 -0.2828526496887207 -0.4550313353538513 -0.010540962219238281 -0.010540962219238281
2.25 -0.25910264253

2.125 -0.16161219775676727 -0.36793360114097595 -0.22692155838012695 -0.22692155838012695
2.0 -0.10071311891078949 -0.35792985558509827 -1.0566856861114502 -1.0566855669021606
2.25 -0.24160213768482208 -0.4477940797805786 -0.1986810564994812 -0.1986810564994812
2.0 -0.16593173146247864 -0.3807508051395416 -0.00014257431030273438 -0.00014257431030273438
2.34375 -0.23743362724781036 -0.41510120034217834 -0.3469959497451782 -0.34699583053588867
2.15625 -0.13139399886131287 -0.354320228099823 -0.1865382194519043 -0.1865382194519043
2.34375 -0.1879003643989563 -0.42159393429756165 -0.006237983703613281 -0.006237983703613281
2.3125 -0.16726669669151306 -0.3676251471042633 -0.00011146068572998047 -0.00011146068572998047
2.28125 -0.1981058567762375 -0.3927671015262604 -0.0020494461059570312 -0.0020494461059570312
2.375 -0.09908745437860489 -0.32546353340148926 -0.002245187759399414 -0.002245187759399414
2.40625 -0.22595106065273285 -0.3805004954338074 -1.3606162071228027 -1.3606152534484863
2.

2.625 -0.3041231036186218 -0.4444815516471863 -0.0010366439819335938 -0.0010366439819335938
2.125 -0.18937647342681885 -0.35498732328414917 -0.12547147274017334 -0.12547147274017334
2.3125 -0.28631532192230225 -0.43010789155960083 -0.00015687942504882812 -0.00015687942504882812
2.1875 -0.2281956672668457 -0.41063040494918823 -1.0352380275726318 -1.0352380275726318
2.1875 -0.18809279799461365 -0.40496981143951416 -1.5234041213989258 -1.523404598236084
1.90625 -0.2130720615386963 -0.41668304800987244 -0.00023555755615234375 -0.00023555755615234375
2.25 -0.18828710913658142 -0.4299594461917877 -1.0876116752624512 -1.0876107215881348
2.1875 -0.19942276179790497 -0.44703948497772217 -0.00771331787109375 -0.00771331787109375
2.28125 -0.1987031102180481 -0.4276491701602936 -0.4947086572647095 -0.4947085976600647
2.34375 -0.17026133835315704 -0.4842706620693207 -0.0017147064208984375 -0.0017147064208984375
2.25 -0.23773930966854095 -0.44318872690200806 -0.16201305389404297 -0.16201305389404297

In [ ]:
train() #same as above but dropout = 0, positive cutoff = -0.6, attempt 2

4.3125 -4.688603401184082 -4.786344528198242 -4.771628379821777 -4.771628379821777
3.4375 -4.484313488006592 -4.767498016357422 -4.5827765464782715 -4.5827765464782715
4.09375 -4.466257572174072 -4.766623497009277 -4.659383296966553 -4.6593828201293945
3.5625 -4.3042426109313965 -4.749497890472412 -4.774873733520508 -4.774873733520508
3.4375 -4.535284519195557 -4.781228542327881 -4.788321495056152 -4.788321495056152
3.9375 -4.54312801361084 -4.7743940353393555 -4.76882266998291 -4.76882266998291
3.5625 -4.561496734619141 -4.775669574737549 -4.872730255126953 -4.872730255126953
3.46875 -4.525303840637207 -4.775633811950684 -4.489707946777344 -4.489707946777344
3.625 -4.446394920349121 -4.756369590759277 -4.810926914215088 -4.81092643737793
3.5 -4.300575256347656 -4.726665496826172 -4.166652679443359 -4.166652202606201
3.5 -4.444095611572266 -4.758523941040039 -4.908621788024902 -4.908621311187744
3.46875 -4.567686557769775 -4.770594120025635 -4.729990482330322 -4.729990482330322
4.03125

3.3125 -4.336357593536377 -4.7452874183654785 -4.483576774597168 -4.483576774597168
3.03125 -4.267536163330078 -4.739245891571045 -5.016447067260742 -5.016447067260742
3.09375 -4.222743034362793 -4.713428497314453 -5.010854244232178 -5.0108537673950195
3.78125 -4.263890266418457 -4.729714870452881 -4.930408477783203 -4.930408000946045
3.5625 -4.3105387687683105 -4.74015474319458 -4.975164413452148 -4.975164413452148
3.59375 -4.292486667633057 -4.7457733154296875 -4.821658134460449 -4.821658134460449
3.25 -4.272652626037598 -4.7262349128723145 -4.396544456481934 -4.396544456481934
3.125 -4.266115665435791 -4.730271816253662 -5.250349998474121 -5.250349998474121
3.4375 -4.3459978103637695 -4.75092077255249 -4.929948806762695 -4.929948329925537
3.0625 -4.386048316955566 -4.753336429595947 -4.974543571472168 -4.974543571472168
3.25 -4.35365104675293 -4.7535600662231445 -4.979988098144531 -4.9799885749816895
3.46875 -4.229846954345703 -4.720418930053711 -5.02569055557251 -5.025690078735352


2.875 -4.3260884284973145 -4.74493408203125 -4.928175926208496 -4.928175926208496
3.1875 -4.283276557922363 -4.7323713302612305 -5.0014448165893555 -5.001444339752197
3.21875 -4.21909236907959 -4.736027240753174 -5.0264668464660645 -5.026466369628906
2.84375 -4.156877517700195 -4.712453842163086 -5.058010101318359 -5.058010101318359
3.21875 -4.215785980224609 -4.708708763122559 -4.969313144683838 -4.969313144683838
3.5 -4.273102760314941 -4.724597454071045 -4.957197666168213 -4.957197666168213
3.21875 -4.367427825927734 -4.750291347503662 -4.952793598175049 -4.952794075012207
3.8125 -4.386920928955078 -4.754484176635742 -4.368586540222168 -4.368587017059326
3.34375 -4.388920783996582 -4.761322021484375 -4.916261672973633 -4.916262149810791
3.28125 -4.35889196395874 -4.746235370635986 -4.9410295486450195 -4.941029071807861
3.15625 -4.301624298095703 -4.734861373901367 -4.9994354248046875 -4.999434471130371
3.21875 -4.253608703613281 -4.71750545501709 -4.987308025360107 -4.98730802536010

3.03125 -4.2409162521362305 -4.727415084838867 -4.997128486633301 -4.997128963470459
3.46875 -4.246864318847656 -4.727524280548096 -4.994174003601074 -4.994173526763916
2.90625 -4.243241310119629 -4.72652006149292 -4.968908309936523 -4.968907833099365
3.0625 -4.216140270233154 -4.721031188964844 -4.223109245300293 -4.223109245300293
3.03125 -4.202838897705078 -4.724623203277588 -5.008657932281494 -5.008658409118652
3.5625 -4.236408233642578 -4.734863758087158 -4.984125137329102 -4.984126091003418
3.1875 -4.24953031539917 -4.731170177459717 -4.264609336853027 -4.264609336853027
3.28125 -4.228684902191162 -4.71936559677124 -4.98715877532959 -4.98715877532959
2.71875 -4.21450138092041 -4.729568958282471 -5.00398063659668 -5.00398063659668
2.96875 -4.216804504394531 -4.7256388664245605 -5.025758266448975 -5.025758743286133
2.9375 -4.231050491333008 -4.729091644287109 -4.98176383972168 -4.98176383972168
3.28125 -4.243001461029053 -4.732280254364014 -4.979976654052734 -4.979976654052734
3.06

3.0 -4.231762886047363 -4.724930286407471 -4.978189945220947 -4.978189945220947
3.3125 -4.204706192016602 -4.7180681228637695 -5.000038146972656 -5.000037670135498
2.75 -4.213923454284668 -4.728423118591309 -4.200274467468262 -4.20027494430542
2.9375 -4.239195346832275 -4.735617637634277 -4.978334903717041 -4.978334903717041
3.4375 -4.256767272949219 -4.73765230178833 -4.988144397735596 -4.9881439208984375
3.0625 -4.219084739685059 -4.737260341644287 -4.23499059677124 -4.234991073608398
3.59375 -4.196098327636719 -4.721395492553711 -4.980833053588867 -4.980833053588867
3.09375 -4.178146839141846 -4.721628189086914 -4.178674697875977 -4.178675174713135
3.3125 -4.208785057067871 -4.713233947753906 -4.9738616943359375 -4.9738616943359375
3.0625 -4.234713077545166 -4.727715015411377 -5.033935546875 -5.033935546875
3.0 -4.244804382324219 -4.726625442504883 -4.954507827758789 -4.954507827758789
2.9375 -4.23073673248291 -4.7243475914001465 -5.016000747680664 -5.016000270843506
3.3125 -4.20974

...

2.90625 -4.188546180725098 -4.734476566314697 -4.213885307312012 -4.213885307312012
2.78125 -4.164498805999756 -4.724084854125977 -5.008882999420166 -5.008882999420166
2.59375 -4.150373458862305 -4.735049247741699 -4.9965972900390625 -4.9965972900390625
2.9375 -4.118716239929199 -4.725024700164795 -4.970015525817871 -4.970016002655029
2.75 -4.205129146575928 -4.726937294006348 -4.9936723709106445 -4.9936723709106445
2.625 -4.168869972229004 -4.733635902404785 -4.984847068786621 -4.984847068786621
2.59375 -4.165489673614502 -4.714297771453857 -4.201915740966797 -4.201915264129639
2.90625 -4.159491539001465 -4.717338562011719 -5.005078315734863 -5.0050787925720215
2.875 -4.18430233001709 -4.715010166168213 -4.217133522033691 -4.217133522033691
2.84375 -4.009108543395996 -4.637279033660889 -4.223463535308838 -4.223463535308838
2.6875 -4.156833648681641 -4.724843502044678 -4.964266777038574 -4.964267253875732
2.75 -4.0812296867370605 -4.699917793273926 -4.2208027839660645 -4.22080278396606

3.46875 -3.9759902954101562 -4.63515567779541 -4.2183451652526855 -4.2183451652526855
3.03125 -3.957695960998535 -4.5307698249816895 -4.194818496704102 -4.194818496704102
2.53125 -3.463726282119751 -4.189413547515869 -3.3429484367370605 -3.3429484367370605
3.125 -3.7145161628723145 -4.300002098083496 -5.014113426208496 -5.014113426208496
2.84375 -3.9895925521850586 -4.607880115509033 -5.004604816436768 -5.004604816436768
3.0 -3.436001777648926 -4.071045875549316 -5.018892288208008 -5.018892288208008
2.90625 -4.0077691078186035 -4.623611927032471 -4.933345794677734 -4.933345794677734
2.8125 -3.7049708366394043 -4.346790790557861 -5.062092304229736 -5.062092304229736
2.65625 -3.88643741607666 -4.442600250244141 -4.996233940124512 -4.996233940124512
2.96875 -3.6465320587158203 -4.3275346755981445 -1.8828771114349365 -1.882877230644226
2.8125 -3.5520756244659424 -4.199146270751953 -0.9977866411209106 -0.9977866411209106
2.9375 -3.7054295539855957 -4.228651523590088 -4.229771137237549 -4.22

2.75 -4.169100761413574 -4.723278522491455 -4.203758716583252 -4.203758716583252
2.625 -4.128599643707275 -4.705205917358398 -4.993093490600586 -4.993093490600586
2.9375 -4.187134742736816 -4.736229419708252 -4.227172374725342 -4.227171897888184
3.15625 -4.113000869750977 -4.679103851318359 -4.99932861328125 -4.99932861328125
2.90625 -4.157001972198486 -4.732885837554932 -4.2134552001953125 -4.2134552001953125
3.0625 -4.180959701538086 -4.723704814910889 -5.006876468658447 -5.006876468658447
2.90625 -4.193844318389893 -4.730254173278809 -5.010756015777588 -5.010756492614746
2.75 -4.198368072509766 -4.732587814331055 -4.356091499328613 -4.356091499328613
2.78125 -4.170714378356934 -4.7284016609191895 -4.200433731079102 -4.200433254241943
3.3125 -4.181741237640381 -4.737571716308594 -4.206978797912598 -4.206978797912598
2.8125 -4.196148872375488 -4.728621006011963 -4.241922855377197 -4.241922378540039
3.21875 -4.165816307067871 -4.73578405380249 -4.953090190887451 -4.953090190887451
2.96

2.96875 -4.119800567626953 -4.695175647735596 -4.368398189544678 -4.368398189544678
2.78125 -4.086239337921143 -4.712380409240723 -4.2193603515625 -4.2193603515625
3.0 -4.199004173278809 -4.730993747711182 -4.970386028289795 -4.970385551452637
2.875 -4.168586730957031 -4.733307838439941 -5.027780532836914 -5.027781009674072
2.78125 -4.151556015014648 -4.72632360458374 -5.004316806793213 -5.004316329956055
2.90625 -4.185643672943115 -4.722720146179199 -4.1956305503845215 -4.1956305503845215
2.90625 -4.198642730712891 -4.738171100616455 -4.189879417419434 -4.189879417419434
3.40625 -4.1712646484375 -4.735543727874756 -4.88314962387085 -4.883150100708008
2.9375 -4.1594109535217285 -4.7200140953063965 -4.197730541229248 -4.197730541229248
2.90625 -4.117466449737549 -4.708039283752441 -4.243127822875977 -4.243127822875977
2.71875 -4.130841255187988 -4.709159851074219 -5.0981340408325195 -5.098134517669678
2.65625 -4.21091365814209 -4.746119499206543 -4.284150123596191 -4.284150123596191
2.8

3.40625 -4.08570671081543 -4.610807418823242 -5.0338945388793945 -5.033894062042236
3.25 -4.055441856384277 -4.570574760437012 -5.003770351409912 -5.003770351409912
2.96875 -3.8801310062408447 -4.446091175079346 -5.039440155029297 -5.039440631866455
2.84375 -3.9825668334960938 -4.549290180206299 -5.000496864318848 -5.000496864318848
3.03125 -4.009427070617676 -4.604517936706543 -5.045244216918945 -5.045244216918945
3.15625 -4.113455772399902 -4.723266124725342 -4.217230319976807 -4.217230319976807
3.0 -4.132943153381348 -4.694493293762207 -4.225314140319824 -4.225314140319824
2.4375 -4.0199689865112305 -4.602015018463135 -4.335875988006592 -4.335875988006592
3.25 -3.973087787628174 -4.527406215667725 -5.098214149475098 -5.098214626312256
2.90625 -3.673440456390381 -4.278548240661621 -5.020469665527344 -5.020469665527344
2.84375 -3.9122061729431152 -4.48723030090332 -5.006538391113281 -5.006538391113281
2.53125 -3.71730375289917 -4.264689922332764 -0.5249061584472656 -0.5249056816101074